# K-Fold CV for Boosting Methods Using SKLearn 

In [1]:
#Importing required libraries
from sklearn.datasets import load_breast_cancer
import pandas as pd
import numpy as np

from sklearn.model_selection import KFold 
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import LeaveOneOut
from sklearn.model_selection import RandomizedSearchCV
from scipy.stats import randint

from sklearn.metrics import accuracy_score
from sklearn.metrics import confusion_matrix, classification_report
from tqdm import tqdm
import wfdb

from sklearn.model_selection import train_test_split
from sklearn.model_selection import LeaveOneOut
from sklearn.model_selection import cross_val_score
from sklearn.linear_model import LinearRegression
from numpy import mean
from numpy import absolute
from numpy import sqrt
import pandas as pd
import random

In [2]:
import xgboost as xgb
from sklearn import metrics
from lightgbm import LGBMClassifier

import lightgbm
import lightgbm as lgb
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelBinarizer

C:\Users\santo\anaconda3\lib\site-packages\xgboost\compat.py:36: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  from pandas import MultiIndex, Int64Index


In [3]:
import matplotlib.pyplot as plt
%matplotlib inline
plt.rcParams['figure.dpi'] = 70 #display 70 dpi in Jupyter Notebook, may consider100 dpi 
plt.rcParams['savefig.dpi'] = 300 #define 300 dpi for saving figures

import seaborn as sns
## here are some settings 
sns.set_style('whitegrid')
sns.set(rc={"figure.dpi":70, 'savefig.dpi':300}) #defining dpi setting
sns.set_context('notebook')
sns.set_style("ticks")
from IPython.display import set_matplotlib_formats

### To load sklearn dataset
sklearn.datasets.load_breast_cancer(*, return_X_y=False, as_frame=False)[source]¶

Load and return the breast cancer wisconsin dataset (classification).

In [4]:
#data = load_breast_cancer(as_frame = True); 
#df = data.frame; 
#print(df.shape)
# In this block use the code we looked at on 6/30 as a reference to save our rr-intervals as a .
rlist = []
records = 'mit-bih-raw\RECORDS' # Replace the _______ with the name of the records file in your MIT-BIH data folder
with open(records) as rfile: #Then we open the file 
                             #The 'with' command only opens the file while we are in it. Automatically closes the file when we're not
    for record in rfile:  # Then we iterate through the lines in the file
        record = record[0:len(record)-1] # Remove any erronious new line characters at the end ('\n')
        rlist.append(record) # Then build an array with it
        

###### Step 1: Initialize all Arrays
             # Below, replace all of the ___ with the command that declares an array/list
             # hint: https://stackoverflow.com/questions/1514553/how-to-declare-an-array-in-python
samples = [] # will house the samples of all subjects
good_list = [] # will list the names of the subjects we successfully extracted
bad_list = [] # will house the names of the subjects we failed to extract
qrs = [] # will house the indices of R-Peaks for all subjects
atr_label = [] # will house the labels for each rhythm annotation for all subjects
atr_locs = [] # will house the locations corresponding to the rhythm annotation labels


###### Step 2: Extract Information
for x in tqdm(rlist): #this will iterate through te records that we found above
  
    try: # A try statement will run the except statement if for some reason the try commands fail
         # In this case I use the try statement because one of the subjects has no signal data causing failure
         # I then use bad_list and good_list so that all of the indices in rlist match with the arrays we initialized in Step 1, above
        ######################################################
            # Below find the wfdb function that will return the information that is described below 
        # Then replace _____ with the correct function call
        samp = wfdb.rdsamp('mit-bih-raw/'+x) # wfdb._____(file_location) will read the signal & header data and return a 2 value array
            # samp[0] - the signal data is the raw reading from the ecg. Each value is a sample taken.
            # samp[1] - the header data includes things about the signal data such as:
              # samples per section, denoted 'fs'
              # number of signals, denoted 'n_sig'
            
        ######################################################
        samples.append(samp) #add it to our array for all subject
            #What is our file extension that has the annotation we want? Find it here and replace _____ with it 
            #hint: READ THE VARIABLE NAMES!!!!
        qrs_tmp = wfdb.rdann('mit-bih-raw/'+x, extension='qrs') #extract the QRS Info
        qrs_locs = np.array(qrs_tmp.sample, dtype='int') #Get just the loccation of R-Peaks from the QRS Info
        qrs.append(qrs_locs) # Add to our array for all subjects
        
            #Do the same thing here
        atr = wfdb.rdann('mit-bih-raw/'+x,extension='atr') #extract the atr info which stores the rhythm type(s) over the whole signal
        atr_label.append(atr.aux_note) # aux_note stores the type of rhythm - main two are '(N' for normal and '(AFIB' for AFIB
        atr_locs.append(np.append(atr.sample, len(samp[0]))) #I add the length of the whole sample to the end for better visualization later
        
        good_list.append(x) # when all extraction is successful append the record name to good_list
    except Exception as exep:
        print(exep) # Alert the user of an exception
        bad_list.append(x) # add to the bad list

        

  0%|          | 0/25 [00:00<?, ?it/s]

sampto must be greater than sampfrom
sampto must be greater than sampfrom


100%|██████████| 25/25 [00:23<00:00,  1.06it/s]


In [5]:
features_df_list = []
for subject in good_list:
    data = pd.read_csv(f'subject-features-dataframes/subject{subject}.csv')
    data = data.assign(Subject = subject)
    #print(data)
    features_df_list.append(data)
#features_maindf = pd.concat(features_df_list, ignore_index = True)

In [6]:
features_maindf = pd.concat(features_df_list, ignore_index = True)
print(features_maindf.columns)

Index(['Unnamed: 0', 'StoS', 'StoR', 'StoL', 'RtoS', 'RtoR', 'RtoL', 'LtoS',
       'LtoR', 'LtoL', 'STD', 'CoefVar', 'Range', 'Volatility', 'ShEn',
       'AppEn', 'SampEn', 'IQR', 'Var', 'Rmean_Var', 'Mean_Absolute_Deviation',
       'Rhythm', 'Subject'],
      dtype='object')


In [7]:
# Short to Short

import lightgbm

#Implementing cross validation 
#kf = KFold(n_splits=23, random_state=1, shuffle=True)
model = lightgbm.LGBMClassifier(learning_rate=0.1, n_estimators=100, max_depth=5, random_state=0)

from time import time
import timeit #imports timeit module
start_time = timeit.default_timer() #defines start time so computational time can be calculated

acc_score = [];
Truth = [];
Output = [];
n_estimators_list = []
max_depth_list = []

x_values = ['StoS']
# 'StoS', 'StoR', 'StoL', 'RtoS', 'RtoR', 'RtoL', 'LtoS',
#        'LtoR', 'LtoL', 'STD', 'CoefVar', 'Range', 'Volatility', 'ShEn',
#        'AppEn', 'SampEn', 'IQR', 'Var', 'Rmean_Var', 'Mean_Absolute_Deviation'
y_values = ['Rhythm']
df = features_maindf

for idx, subject in enumerate(good_list):
    
    train_index = ~df['Subject'].str.contains(subject)
    test_index = df['Subject'].str.contains(subject)
    X_train , X_test = df.loc[train_index,x_values], df.loc[test_index,x_values]
    y_train , y_test = df.loc[train_index,y_values].values.ravel(), df.loc[test_index,y_values]

    # Create the LightGBM data containers
    model.fit(X_train,y_train,eval_set=[(X_test,y_test),(X_train,y_train)],
          eval_metric='logloss')

    pred_values = model.predict(X_test)
     
    acc = accuracy_score(y_test, pred_values)
    acc_score.append(acc)
    
    Truth.extend(y_test.values.reshape(y_test.shape[0])); ## it is a list
    Output.extend(pred_values); ## it is a list  
    
    #print(model.feature_importances_)
#     Importance = pd.DataFrame({'Importance':(model.feature_importances_*100)}, 
#                           index = (X_train.columns))
#     Importance.sort_values(by = 'Importance', 
#                        axis = 0, 
#                        ascending = True).plot(kind = 'barh', 
#                                               color = 'r')
#     plt.xlabel('Variable Importance')
#     plt.gca().legend_ = None
    #plt.savefig('plot1.png')


elapsed = timeit.default_timer() - start_time #gives total computation time
print("---Run time is %s seconds ---" % elapsed) #prints computation time
print()

print('Accuracy of each fold: \n {}'.format(acc_score))
print()
print('Avg accuracy : \n{}'.format(np.mean(acc_score))); 
print()
print('Std of accuracy : \n{}'.format(np.std(acc_score)))

print(confusion_matrix(Truth, Output))
print(classification_report(Truth, Output))
print(acc_score)
print(elapsed)

[1]	training's binary_logloss: 0.663169	valid_0's binary_logloss: 0.583485


C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[2]	training's binary_logloss: 0.640457	valid_0's binary_logloss: 0.543097
[3]	training's binary_logloss: 0.621773	valid_0's binary_logloss: 0.508882
[4]	training's binary_logloss: 0.606301	valid_0's binary_logloss: 0.479678
[5]	training's binary_logloss: 0.593425	valid_0's binary_logloss: 0.454601
[6]	training's binary_logloss: 0.58267	valid_0's binary_logloss: 0.432963
[7]	training's binary_logloss: 0.573665	valid_0's binary_logloss: 0.414217
[8]	training's binary_logloss: 0.566112	valid_0's binary_logloss: 0.397925
[9]	training's binary_logloss: 0.559769	valid_0's binary_logloss: 0.383726
[10]	training's binary_logloss: 0.55444	valid_0's binary_logloss: 0.371324
[11]	training's binary_logloss: 0.549961	valid_0's binary_logloss: 0.360472
[12]	training's binary_logloss: 0.546199	valid_0's binary_logloss: 0.350961
[13]	training's binary_logloss: 0.543039	valid_0's binary_logloss: 0.342617
[14]	training's binary_logloss: 0.540387	valid_0's binary_logloss: 0.335289
[15]	training's binary

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.657848	valid_0's binary_logloss: 0.669395
[2]	training's binary_logloss: 0.631386	valid_0's binary_logloss: 0.683584
[3]	training's binary_logloss: 0.609616	valid_0's binary_logloss: 0.697856
[4]	training's binary_logloss: 0.591586	valid_0's binary_logloss: 0.711926
[5]	training's binary_logloss: 0.576581	valid_0's binary_logloss: 0.725602
[6]	training's binary_logloss: 0.564049	valid_0's binary_logloss: 0.738756
[7]	training's binary_logloss: 0.553557	valid_0's binary_logloss: 0.751305
[8]	training's binary_logloss: 0.544757	valid_0's binary_logloss: 0.763198
[9]	training's binary_logloss: 0.537369	valid_0's binary_logloss: 0.774409
[10]	training's binary_logloss: 0.531162	valid_0's binary_logloss: 0.784925
[11]	training's binary_logloss: 0.525948	valid_0's binary_logloss: 0.794752
[12]	training's binary_logloss: 0.521568	valid_0's binary_logloss: 0.803903
[13]	training's binary_logloss: 0.517891	valid_0's binary_logloss: 0.812396
[14]	training's binar

...

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.6568	valid_0's binary_logloss: 0.720763
[2]	training's binary_logloss: 0.634637	valid_0's binary_logloss: 0.676623
[3]	training's binary_logloss: 0.616419	valid_0's binary_logloss: 0.639643
[4]	training's binary_logloss: 0.601346	valid_0's binary_logloss: 0.608293
[5]	training's binary_logloss: 0.588818	valid_0's binary_logloss: 0.581472
[6]	training's binary_logloss: 0.578371	valid_0's binary_logloss: 0.558355
[7]	training's binary_logloss: 0.569639	valid_0's binary_logloss: 0.538314
[8]	training's binary_logloss: 0.562329	valid_0's binary_logloss: 0.520851
[9]	training's binary_logloss: 0.556204	valid_0's binary_logloss: 0.505573
[10]	training's binary_logloss: 0.55107	valid_0's binary_logloss: 0.492159
[11]	training's binary_logloss: 0.546767	valid_0's binary_logloss: 0.480346
[12]	training's binary_logloss: 0.543161	valid_0's binary_logloss: 0.469917
[13]	training's binary_logloss: 0.540142	valid_0's binary_logloss: 0.460688
[14]	training's binary_l

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.663015	valid_0's binary_logloss: 0.578476
[2]	training's binary_logloss: 0.640556	valid_0's binary_logloss: 0.532923
[3]	training's binary_logloss: 0.622083	valid_0's binary_logloss: 0.493973
[4]	training's binary_logloss: 0.60679	valid_0's binary_logloss: 0.460412
[5]	training's binary_logloss: 0.594067	valid_0's binary_logloss: 0.431312
[6]	training's binary_logloss: 0.583445	valid_0's binary_logloss: 0.405949
[7]	training's binary_logloss: 0.574556	valid_0's binary_logloss: 0.383746
[8]	training's binary_logloss: 0.567104	valid_0's binary_logloss: 0.364239
[9]	training's binary_logloss: 0.560851	valid_0's binary_logloss: 0.347045
[10]	training's binary_logloss: 0.555601	valid_0's binary_logloss: 0.331852
[11]	training's binary_logloss: 0.551192	valid_0's binary_logloss: 0.318394
[12]	training's binary_logloss: 0.547492	valid_0's binary_logloss: 0.306451
[13]	training's binary_logloss: 0.544387	valid_0's binary_logloss: 0.295833
[14]	training's binary

              precision    recall  f1-score   support

           0       0.73      0.62      0.67     24743
           1       0.61      0.73      0.66     20225

    accuracy                           0.67     44968
   macro avg       0.67      0.67      0.67     44968
weighted avg       0.68      0.67      0.67     44968

[0.8483981693363845, 0.24178498985801217, 0.9861460957178841, 0.8920863309352518, 0.8359456635318704, 0.09776876267748479, 0.6202709014479215, 0.9904697072838666, 0.7399598393574297, 0.7276736493936052, 0.6311252268602541, 0.9849246231155779, 0.6063492063492063, 0.3159235668789809, 0.5645295587010825, 0.8817013735046522, 0.9129540781357094, 0.31217541834968265, 0.2569737954353339, 0.8290269378779549, 0.8387510692899914, 0.9648462021343377, 0.852431289640592]
5.133077199999999


In [8]:
# Short to Regular

import lightgbm

#Implementing cross validation 
#kf = KFold(n_splits=23, random_state=1, shuffle=True)
model = lightgbm.LGBMClassifier(learning_rate=0.1, n_estimators=100, max_depth=5, random_state=0)

from time import time
import timeit #imports timeit module
start_time = timeit.default_timer() #defines start time so computational time can be calculated

acc_score = [];
Truth = [];
Output = [];
n_estimators_list = []
max_depth_list = []

x_values = ['StoR']
# 'StoS', 'StoR', 'StoL', 'RtoS', 'RtoR', 'RtoL', 'LtoS',
#        'LtoR', 'LtoL', 'STD', 'CoefVar', 'Range', 'Volatility', 'ShEn',
#        'AppEn', 'SampEn', 'IQR', 'Var', 'Rmean_Var', 'Mean_Absolute_Deviation'
y_values = ['Rhythm']
df = features_maindf

for idx, subject in enumerate(good_list):
    
    train_index = ~df['Subject'].str.contains(subject)
    test_index = df['Subject'].str.contains(subject)
    X_train , X_test = df.loc[train_index,x_values], df.loc[test_index,x_values]
    y_train , y_test = df.loc[train_index,y_values].values.ravel(), df.loc[test_index,y_values]

    # Create the LightGBM data containers
    model.fit(X_train,y_train,eval_set=[(X_test,y_test),(X_train,y_train)],
          eval_metric='logloss')

    pred_values = model.predict(X_test)
     
    acc = accuracy_score(y_test, pred_values)
    acc_score.append(acc)
    
    Truth.extend(y_test.values.reshape(y_test.shape[0])); ## it is a list
    Output.extend(pred_values); ## it is a list  
    
    #print(model.feature_importances_)
#     Importance = pd.DataFrame({'Importance':(model.feature_importances_*100)}, 
#                           index = (X_train.columns))
#     Importance.sort_values(by = 'Importance', 
#                        axis = 0, 
#                        ascending = True).plot(kind = 'barh', 
#                                               color = 'r')
#     plt.xlabel('Variable Importance')
#     plt.gca().legend_ = None
    #plt.savefig('plot1.png')


elapsed = timeit.default_timer() - start_time #gives total computation time
print("---Run time is %s seconds ---" % elapsed) #prints computation time
print()

print('Accuracy of each fold: \n {}'.format(acc_score))
print()
print('Avg accuracy : \n{}'.format(np.mean(acc_score))); 
print()
print('Std of accuracy : \n{}'.format(np.std(acc_score)))

print(confusion_matrix(Truth, Output))
print(classification_report(Truth, Output))
print(acc_score)
print(elapsed)

[1]	training's binary_logloss: 0.628865	valid_0's binary_logloss: 0.574288
[2]	training's binary_logloss: 0.578104	valid_0's binary_logloss: 0.527818
[3]	training's binary_logloss: 0.536084	valid_0's binary_logloss: 0.489706
[4]	training's binary_logloss: 0.500943	valid_0's binary_logloss: 0.458188
[5]	training's binary_logloss: 0.471326	valid_0's binary_logloss: 0.431972
[6]	training's binary_logloss: 0.446215	valid_0's binary_logloss: 0.410078
[7]	training's binary_logloss: 0.424824	valid_0's binary_logloss: 0.391751
[8]	training's binary_logloss: 0.406536	valid_0's binary_logloss: 0.37639
[9]	training's binary_logloss: 0.390856	valid_0's binary_logloss: 0.363517
[10]	training's binary_logloss: 0.377381	valid_0's binary_logloss: 0.352738
[11]	training's binary_logloss: 0.365782	valid_0's binary_logloss: 0.343732
[12]	training's binary_logloss: 0.355785	valid_0's binary_logloss: 0.33623
[13]	training's binary_logloss: 0.347159	valid_0's binary_logloss: 0.330006
[14]	training's binary_

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.628875	valid_0's binary_logloss: 0.600632
[2]	training's binary_logloss: 0.578717	valid_0's binary_logloss: 0.554643
[3]	training's binary_logloss: 0.537196	valid_0's binary_logloss: 0.515834
[4]	training's binary_logloss: 0.502469	valid_0's binary_logloss: 0.482812
[5]	training's binary_logloss: 0.473198	valid_0's binary_logloss: 0.454528
[6]	training's binary_logloss: 0.448375	valid_0's binary_logloss: 0.430176
[7]	training's binary_logloss: 0.427224	valid_0's binary_logloss: 0.409119
[8]	training's binary_logloss: 0.409135	valid_0's binary_logloss: 0.390847
[9]	training's binary_logloss: 0.393618	valid_0's binary_logloss: 0.374946
[10]	training's binary_logloss: 0.380277	valid_0's binary_logloss: 0.361075
[11]	training's binary_logloss: 0.368785	valid_0's binary_logloss: 0.348949
[12]	training's binary_logloss: 0.358871	valid_0's binary_logloss: 0.338333
[13]	training's binary_logloss: 0.35031	valid_0's binary_logloss: 0.329024
[14]	training's binary

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.629889	valid_0's binary_logloss: 0.551116
[2]	training's binary_logloss: 0.580172	valid_0's binary_logloss: 0.48646
[3]	training's binary_logloss: 0.539029	valid_0's binary_logloss: 0.431967
[4]	training's binary_logloss: 0.504639	valid_0's binary_logloss: 0.385533
[5]	training's binary_logloss: 0.475672	valid_0's binary_logloss: 0.345624
[6]	training's binary_logloss: 0.451131	valid_0's binary_logloss: 0.311082
[7]	training's binary_logloss: 0.430244	valid_0's binary_logloss: 0.281012
[8]	training's binary_logloss: 0.412404	valid_0's binary_logloss: 0.254709
[9]	training's binary_logloss: 0.397123	valid_0's binary_logloss: 0.23161
[10]	training's binary_logloss: 0.384007	valid_0's binary_logloss: 0.211253
[11]	training's binary_logloss: 0.372731	valid_0's binary_logloss: 0.193261
[12]	training's binary_logloss: 0.363023	valid_0's binary_logloss: 0.177319
[13]	training's binary_logloss: 0.35466	valid_0's binary_logloss: 0.163162
[14]	training's binary_l

...

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.629717	valid_0's binary_logloss: 0.554009
[2]	training's binary_logloss: 0.580035	valid_0's binary_logloss: 0.488949
[3]	training's binary_logloss: 0.538923	valid_0's binary_logloss: 0.434091
[4]	training's binary_logloss: 0.504559	valid_0's binary_logloss: 0.387329
[5]	training's binary_logloss: 0.475616	valid_0's binary_logloss: 0.347123
[6]	training's binary_logloss: 0.451095	valid_0's binary_logloss: 0.31231
[7]	training's binary_logloss: 0.430226	valid_0's binary_logloss: 0.281993
[8]	training's binary_logloss: 0.4124	valid_0's binary_logloss: 0.255466
[9]	training's binary_logloss: 0.397133	valid_0's binary_logloss: 0.23216
[10]	training's binary_logloss: 0.384029	valid_0's binary_logloss: 0.211614
[11]	training's binary_logloss: 0.372762	valid_0's binary_logloss: 0.193449
[12]	training's binary_logloss: 0.363064	valid_0's binary_logloss: 0.177346
[13]	training's binary_logloss: 0.354708	valid_0's binary_logloss: 0.163041
[14]	training's binary_lo

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.623676	valid_0's binary_logloss: 0.686933
[2]	training's binary_logloss: 0.574322	valid_0's binary_logloss: 0.621688
[3]	training's binary_logloss: 0.533545	valid_0's binary_logloss: 0.567337
[4]	training's binary_logloss: 0.499494	valid_0's binary_logloss: 0.521466
[5]	training's binary_logloss: 0.47083	valid_0's binary_logloss: 0.482364
[6]	training's binary_logloss: 0.446553	valid_0's binary_logloss: 0.448769
[7]	training's binary_logloss: 0.425891	valid_0's binary_logloss: 0.419723
[8]	training's binary_logloss: 0.408242	valid_0's binary_logloss: 0.394481
[9]	training's binary_logloss: 0.393122	valid_0's binary_logloss: 0.372448
[10]	training's binary_logloss: 0.380138	valid_0's binary_logloss: 0.35315
[11]	training's binary_logloss: 0.368969	valid_0's binary_logloss: 0.336193
[12]	training's binary_logloss: 0.359348	valid_0's binary_logloss: 0.321256
[13]	training's binary_logloss: 0.351052	valid_0's binary_logloss: 0.308068
[14]	training's binary_

              precision    recall  f1-score   support

           0       0.94      0.86      0.90     24743
           1       0.84      0.93      0.89     20225

    accuracy                           0.89     44968
   macro avg       0.89      0.90      0.89     44968
weighted avg       0.90      0.89      0.89     44968

[0.8604118993135011, 0.9294117647058824, 0.9861460957178841, 0.7685851318944844, 0.9848484848484849, 0.9046653144016227, 0.8752919196637086, 0.9891082368958475, 0.9126506024096386, 0.8930540242557883, 0.97005444646098, 0.9655419956927495, 0.5714285714285714, 0.9426751592356688, 0.8397169025811824, 0.9109437306158618, 0.980123372172721, 0.9249855741488748, 0.5832628909551987, 0.9417262231995602, 0.9666381522668948, 0.9918392969240427, 0.9733615221987315]
5.246920199999998


In [9]:
# Short to Long

import lightgbm

#Implementing cross validation 
#kf = KFold(n_splits=23, random_state=1, shuffle=True)
model = lightgbm.LGBMClassifier(learning_rate=0.1, n_estimators=100, max_depth=5, random_state=0)

from time import time
import timeit #imports timeit module
start_time = timeit.default_timer() #defines start time so computational time can be calculated

acc_score = [];
Truth = [];
Output = [];
n_estimators_list = []
max_depth_list = []

x_values = ['StoL']
# 'StoS', 'StoR', 'StoL', 'RtoS', 'RtoR', 'RtoL', 'LtoS',
#        'LtoR', 'LtoL', 'STD', 'CoefVar', 'Range', 'Volatility', 'ShEn',
#        'AppEn', 'SampEn', 'IQR', 'Var', 'Rmean_Var', 'Mean_Absolute_Deviation'
y_values = ['Rhythm']
df = features_maindf

for idx, subject in enumerate(good_list):
    
    train_index = ~df['Subject'].str.contains(subject)
    test_index = df['Subject'].str.contains(subject)
    X_train , X_test = df.loc[train_index,x_values], df.loc[test_index,x_values]
    y_train , y_test = df.loc[train_index,y_values].values.ravel(), df.loc[test_index,y_values]

    # Create the LightGBM data containers
    model.fit(X_train,y_train,eval_set=[(X_test,y_test),(X_train,y_train)],
          eval_metric='logloss')

    pred_values = model.predict(X_test)
     
    acc = accuracy_score(y_test, pred_values)
    acc_score.append(acc)
    
    Truth.extend(y_test.values.reshape(y_test.shape[0])); ## it is a list
    Output.extend(pred_values); ## it is a list  
    
    #print(model.feature_importances_)
#     Importance = pd.DataFrame({'Importance':(model.feature_importances_*100)}, 
#                           index = (X_train.columns))
#     Importance.sort_values(by = 'Importance', 
#                        axis = 0, 
#                        ascending = True).plot(kind = 'barh', 
#                                               color = 'r')
#     plt.xlabel('Variable Importance')
#     plt.gca().legend_ = None
    #plt.savefig('plot1.png')


elapsed = timeit.default_timer() - start_time #gives total computation time
print("---Run time is %s seconds ---" % elapsed) #prints computation time
print()

print('Accuracy of each fold: \n {}'.format(acc_score))
print()
print('Avg accuracy : \n{}'.format(np.mean(acc_score))); 
print()
print('Std of accuracy : \n{}'.format(np.std(acc_score)))

print(confusion_matrix(Truth, Output))
print(classification_report(Truth, Output))
print(acc_score)
print(elapsed)

[1]	training's binary_logloss: 0.675101	valid_0's binary_logloss: 0.611213
[2]	training's binary_logloss: 0.6622	valid_0's binary_logloss: 0.593713
[3]	training's binary_logloss: 0.651709	valid_0's binary_logloss: 0.578652
[4]	training's binary_logloss: 0.643151	valid_0's binary_logloss: 0.565653
[5]	training's binary_logloss: 0.636154	valid_0's binary_logloss: 0.554405
[6]	training's binary_logloss: 0.630425	valid_0's binary_logloss: 0.54465
[7]	training's binary_logloss: 0.625729	valid_0's binary_logloss: 0.536173
[8]	training's binary_logloss: 0.621877	valid_0's binary_logloss: 0.528793
[9]	training's binary_logloss: 0.618716	valid_0's binary_logloss: 0.522355
[10]	training's binary_logloss: 0.616123	valid_0's binary_logloss: 0.516731
[11]	training's binary_logloss: 0.613995	valid_0's binary_logloss: 0.511809
[12]	training's binary_logloss: 0.61225	valid_0's binary_logloss: 0.507495
[13]	training's binary_logloss: 0.610818	valid_0's binary_logloss: 0.503709
[14]	training's binary_lo

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.674782	valid_0's binary_logloss: 0.633166
[2]	training's binary_logloss: 0.662221	valid_0's binary_logloss: 0.613883
[3]	training's binary_logloss: 0.652012	valid_0's binary_logloss: 0.59731
[4]	training's binary_logloss: 0.643689	valid_0's binary_logloss: 0.583002
[5]	training's binary_logloss: 0.636888	valid_0's binary_logloss: 0.570604
[6]	training's binary_logloss: 0.631323	valid_0's binary_logloss: 0.559825
[7]	training's binary_logloss: 0.626764	valid_0's binary_logloss: 0.550428
[8]	training's binary_logloss: 0.623027	valid_0's binary_logloss: 0.542212
[9]	training's binary_logloss: 0.619963	valid_0's binary_logloss: 0.535013
[10]	training's binary_logloss: 0.61745	valid_0's binary_logloss: 0.528691
[11]	training's binary_logloss: 0.615389	valid_0's binary_logloss: 0.523128
[12]	training's binary_logloss: 0.6137	valid_0's binary_logloss: 0.518225
[13]	training's binary_logloss: 0.612316	valid_0's binary_logloss: 0.513896
[14]	training's binary_lo

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.674996	valid_0's binary_logloss: 0.606016
[2]	training's binary_logloss: 0.662218	valid_0's binary_logloss: 0.586212
[3]	training's binary_logloss: 0.651829	valid_0's binary_logloss: 0.569027
[4]	training's binary_logloss: 0.643356	valid_0's binary_logloss: 0.554067
[5]	training's binary_logloss: 0.63643	valid_0's binary_logloss: 0.541008
[6]	training's binary_logloss: 0.630761	valid_0's binary_logloss: 0.52958
[7]	training's binary_logloss: 0.626115	valid_0's binary_logloss: 0.519559
[8]	training's binary_logloss: 0.622305	valid_0's binary_logloss: 0.510753
[9]	training's binary_logloss: 0.61918	valid_0's binary_logloss: 0.503002
[10]	training's binary_logloss: 0.616617	valid_0's binary_logloss: 0.496168
[11]	training's binary_logloss: 0.614514	valid_0's binary_logloss: 0.490133
[12]	training's binary_logloss: 0.61279	valid_0's binary_logloss: 0.484796
[13]	training's binary_logloss: 0.611376	valid_0's binary_logloss: 0.480071
[14]	training's binary_lo

...

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.673503	valid_0's binary_logloss: 0.636712
[2]	training's binary_logloss: 0.660452	valid_0's binary_logloss: 0.62133
[3]	training's binary_logloss: 0.649847	valid_0's binary_logloss: 0.608265
[4]	training's binary_logloss: 0.641201	valid_0's binary_logloss: 0.597121
[5]	training's binary_logloss: 0.634136	valid_0's binary_logloss: 0.587583
[6]	training's binary_logloss: 0.628353	valid_0's binary_logloss: 0.579391
[7]	training's binary_logloss: 0.623615	valid_0's binary_logloss: 0.572336
[8]	training's binary_logloss: 0.619731	valid_0's binary_logloss: 0.566245
[9]	training's binary_logloss: 0.616545	valid_0's binary_logloss: 0.560971
[10]	training's binary_logloss: 0.613932	valid_0's binary_logloss: 0.556395
[11]	training's binary_logloss: 0.611788	valid_0's binary_logloss: 0.552416
[12]	training's binary_logloss: 0.61003	valid_0's binary_logloss: 0.548948
[13]	training's binary_logloss: 0.608589	valid_0's binary_logloss: 0.54592
[14]	training's binary_l

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.674475	valid_0's binary_logloss: 0.613388
[2]	training's binary_logloss: 0.661448	valid_0's binary_logloss: 0.597311
[3]	training's binary_logloss: 0.650857	valid_0's binary_logloss: 0.58357
[4]	training's binary_logloss: 0.64222	valid_0's binary_logloss: 0.571789
[5]	training's binary_logloss: 0.63516	valid_0's binary_logloss: 0.561662
[6]	training's binary_logloss: 0.62938	valid_0's binary_logloss: 0.552936
[7]	training's binary_logloss: 0.624643	valid_0's binary_logloss: 0.5454
[8]	training's binary_logloss: 0.620759	valid_0's binary_logloss: 0.538878
[9]	training's binary_logloss: 0.617572	valid_0's binary_logloss: 0.533224
[10]	training's binary_logloss: 0.614958	valid_0's binary_logloss: 0.528313
[11]	training's binary_logloss: 0.612814	valid_0's binary_logloss: 0.524039
[12]	training's binary_logloss: 0.611055	valid_0's binary_logloss: 0.520315
[13]	training's binary_logloss: 0.609613	valid_0's binary_logloss: 0.517063
[14]	training's binary_logl

              precision    recall  f1-score   support

           0       0.70      0.81      0.75     24743
           1       0.72      0.58      0.64     20225

    accuracy                           0.71     44968
   macro avg       0.71      0.70      0.70     44968
weighted avg       0.71      0.71      0.70     44968

[0.8907322654462243, 0.860446247464503, 0.9219143576826196, 0.710431654676259, 0.754440961337513, 0.8677484787018256, 0.6795889771134984, 0.94213750850919, 0.5737951807228916, 0.6306504961411246, 0.7078039927404719, 0.7753050969131371, 0.6621315192743764, 0.7490445859872611, 0.2402164862614488, 0.6566238369517058, 0.7786154900616861, 0.6237738026543566, 0.39391377852916315, 0.8053875755909841, 0.7869974337040205, 0.8606403013182674, 0.7128964059196617]
4.718778300000004


In [10]:
# Regular to Short

import lightgbm

#Implementing cross validation 
#kf = KFold(n_splits=23, random_state=1, shuffle=True)
model = lightgbm.LGBMClassifier(learning_rate=0.1, n_estimators=100, max_depth=5, random_state=0)

from time import time
import timeit #imports timeit module
start_time = timeit.default_timer() #defines start time so computational time can be calculated

acc_score = [];
Truth = [];
Output = [];
n_estimators_list = []
max_depth_list = []

x_values = ['RtoS']
# 'StoS', 'StoR', 'StoL', 'RtoS', 'RtoR', 'RtoL', 'LtoS',
#        'LtoR', 'LtoL', 'STD', 'CoefVar', 'Range', 'Volatility', 'ShEn',
#        'AppEn', 'SampEn', 'IQR', 'Var', 'Rmean_Var', 'Mean_Absolute_Deviation'
y_values = ['Rhythm']
df = features_maindf

for idx, subject in enumerate(good_list):
    
    train_index = ~df['Subject'].str.contains(subject)
    test_index = df['Subject'].str.contains(subject)
    X_train , X_test = df.loc[train_index,x_values], df.loc[test_index,x_values]
    y_train , y_test = df.loc[train_index,y_values].values.ravel(), df.loc[test_index,y_values]

    # Create the LightGBM data containers
    model.fit(X_train,y_train,eval_set=[(X_test,y_test),(X_train,y_train)],
          eval_metric='logloss')

    pred_values = model.predict(X_test)
     
    acc = accuracy_score(y_test, pred_values)
    acc_score.append(acc)
    
    Truth.extend(y_test.values.reshape(y_test.shape[0])); ## it is a list
    Output.extend(pred_values); ## it is a list  
    
    #print(model.feature_importances_)
#     Importance = pd.DataFrame({'Importance':(model.feature_importances_*100)}, 
#                           index = (X_train.columns))
#     Importance.sort_values(by = 'Importance', 
#                        axis = 0, 
#                        ascending = True).plot(kind = 'barh', 
#                                               color = 'r')
#     plt.xlabel('Variable Importance')
#     plt.gca().legend_ = None
    #plt.savefig('plot1.png')


elapsed = timeit.default_timer() - start_time #gives total computation time
print("---Run time is %s seconds ---" % elapsed) #prints computation time
print()

print('Accuracy of each fold: \n {}'.format(acc_score))
print()
print('Avg accuracy : \n{}'.format(np.mean(acc_score))); 
print()
print('Std of accuracy : \n{}'.format(np.std(acc_score)))

print(confusion_matrix(Truth, Output))
print(classification_report(Truth, Output))
print(acc_score)
print(elapsed)

[1]	training's binary_logloss: 0.641953	valid_0's binary_logloss: 0.580267
[2]	training's binary_logloss: 0.601847	valid_0's binary_logloss: 0.53834
[3]	training's binary_logloss: 0.568696	valid_0's binary_logloss: 0.503697
[4]	training's binary_logloss: 0.541058	valid_0's binary_logloss: 0.474813
[5]	training's binary_logloss: 0.517865	valid_0's binary_logloss: 0.450559
[6]	training's binary_logloss: 0.498306	valid_0's binary_logloss: 0.43008
[7]	training's binary_logloss: 0.481749	valid_0's binary_logloss: 0.41271
[8]	training's binary_logloss: 0.467694	valid_0's binary_logloss: 0.397923
[9]	training's binary_logloss: 0.455739	valid_0's binary_logloss: 0.385297
[10]	training's binary_logloss: 0.445555	valid_0's binary_logloss: 0.374486
[11]	training's binary_logloss: 0.436859	valid_0's binary_logloss: 0.365196
[12]	training's binary_logloss: 0.42944	valid_0's binary_logloss: 0.357238
[13]	training's binary_logloss: 0.423118	valid_0's binary_logloss: 0.350368
[14]	training's binary_lo

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.642285	valid_0's binary_logloss: 0.594955
[2]	training's binary_logloss: 0.603053	valid_0's binary_logloss: 0.544485
[3]	training's binary_logloss: 0.570627	valid_0's binary_logloss: 0.502026
[4]	training's binary_logloss: 0.543597	valid_0's binary_logloss: 0.465969
[5]	training's binary_logloss: 0.52092	valid_0's binary_logloss: 0.43512
[6]	training's binary_logloss: 0.501801	valid_0's binary_logloss: 0.408568
[7]	training's binary_logloss: 0.485622	valid_0's binary_logloss: 0.385604
[8]	training's binary_logloss: 0.471892	valid_0's binary_logloss: 0.365663
[9]	training's binary_logloss: 0.460216	valid_0's binary_logloss: 0.34829
[10]	training's binary_logloss: 0.450273	valid_0's binary_logloss: 0.333112
[11]	training's binary_logloss: 0.441797	valid_0's binary_logloss: 0.319822
[12]	training's binary_logloss: 0.434557	valid_0's binary_logloss: 0.308146
[13]	training's binary_logloss: 0.42838	valid_0's binary_logloss: 0.297887
[14]	training's binary_lo

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.642691	valid_0's binary_logloss: 0.562946
[2]	training's binary_logloss: 0.60339	valid_0's binary_logloss: 0.507831
[3]	training's binary_logloss: 0.570905	valid_0's binary_logloss: 0.461194
[4]	training's binary_logloss: 0.543827	valid_0's binary_logloss: 0.421333
[5]	training's binary_logloss: 0.521109	valid_0's binary_logloss: 0.386992
[6]	training's binary_logloss: 0.501956	valid_0's binary_logloss: 0.357213
[7]	training's binary_logloss: 0.485749	valid_0's binary_logloss: 0.33125
[8]	training's binary_logloss: 0.471996	valid_0's binary_logloss: 0.308513
[9]	training's binary_logloss: 0.460301	valid_0's binary_logloss: 0.288524
[10]	training's binary_logloss: 0.450342	valid_0's binary_logloss: 0.270894
[11]	training's binary_logloss: 0.441842	valid_0's binary_logloss: 0.255302
[12]	training's binary_logloss: 0.434593	valid_0's binary_logloss: 0.241478
[13]	training's binary_logloss: 0.428409	valid_0's binary_logloss: 0.229197
[14]	training's binary_

...

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[2]	training's binary_logloss: 0.601613	valid_0's binary_logloss: 0.548985
[3]	training's binary_logloss: 0.568893	valid_0's binary_logloss: 0.508608
[4]	training's binary_logloss: 0.541614	valid_0's binary_logloss: 0.474363
[5]	training's binary_logloss: 0.518724	valid_0's binary_logloss: 0.445103
[6]	training's binary_logloss: 0.499421	valid_0's binary_logloss: 0.419956
[7]	training's binary_logloss: 0.483083	valid_0's binary_logloss: 0.398238
[8]	training's binary_logloss: 0.469215	valid_0's binary_logloss: 0.379409
[9]	training's binary_logloss: 0.457419	valid_0's binary_logloss: 0.36303
[10]	training's binary_logloss: 0.44737	valid_0's binary_logloss: 0.348744
[11]	training's binary_logloss: 0.438802	valid_0's binary_logloss: 0.336255
[12]	training's binary_logloss: 0.431492	valid_0's binary_logloss: 0.325316
[13]	training's binary_logloss: 0.425245	valid_0's binary_logloss: 0.315657
[14]	training's binary_logloss: 0.419914	valid_0's binary_logloss: 0.307198
[15]	training's binary

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.641689	valid_0's binary_logloss: 0.578126
[2]	training's binary_logloss: 0.601745	valid_0's binary_logloss: 0.533679
[3]	training's binary_logloss: 0.568727	valid_0's binary_logloss: 0.496757
[4]	training's binary_logloss: 0.541199	valid_0's binary_logloss: 0.465808
[5]	training's binary_logloss: 0.518099	valid_0's binary_logloss: 0.439681
[6]	training's binary_logloss: 0.498619	valid_0's binary_logloss: 0.4175
[7]	training's binary_logloss: 0.482128	valid_0's binary_logloss: 0.398582
[8]	training's binary_logloss: 0.468129	valid_0's binary_logloss: 0.382387
[9]	training's binary_logloss: 0.456222	valid_0's binary_logloss: 0.368479
[10]	training's binary_logloss: 0.446077	valid_0's binary_logloss: 0.356504
[11]	training's binary_logloss: 0.437428	valid_0's binary_logloss: 0.346169
[12]	training's binary_logloss: 0.430048	valid_0's binary_logloss: 0.337232
[13]	training's binary_logloss: 0.423752	valid_0's binary_logloss: 0.329489
[14]	training's binary_

              precision    recall  f1-score   support

           0       0.87      0.83      0.85     24743
           1       0.80      0.84      0.82     20225

    accuracy                           0.84     44968
   macro avg       0.83      0.84      0.84     44968
weighted avg       0.84      0.84      0.84     44968

[0.8689931350114416, 0.911156186612576, 0.9836272040302267, 0.6804556354916067, 0.9409613375130617, 0.908316430020284, 0.8397944885567492, 0.9782164737916951, 0.8664658634538153, 0.705071664829107, 0.9428312159709619, 0.9332376166547021, 0.6267573696145124, 0.9299363057324841, 0.5603663613655288, 0.8156845369960124, 0.9225496915695682, 0.9203693017888055, 0.4974640743871513, 0.9081913139087411, 0.916595380667237, 0.8807281858129316, 0.904016913319239]
4.687473500000003


In [11]:
# Regular to Regular

import lightgbm

#Implementing cross validation 
#kf = KFold(n_splits=23, random_state=1, shuffle=True)
model = lightgbm.LGBMClassifier(learning_rate=0.1, n_estimators=100, max_depth=5, random_state=0)

from time import time
import timeit #imports timeit module
start_time = timeit.default_timer() #defines start time so computational time can be calculated

acc_score = [];
Truth = [];
Output = [];
n_estimators_list = []
max_depth_list = []

x_values = ['RtoR']
# 'StoS', 'StoR', 'StoL', 'RtoS', 'RtoR', 'RtoL', 'LtoS',
#        'LtoR', 'LtoL', 'STD', 'CoefVar', 'Range', 'Volatility', 'ShEn',
#        'AppEn', 'SampEn', 'IQR', 'Var', 'Rmean_Var', 'Mean_Absolute_Deviation'
y_values = ['Rhythm']
df = features_maindf

for idx, subject in enumerate(good_list):
    
    train_index = ~df['Subject'].str.contains(subject)
    test_index = df['Subject'].str.contains(subject)
    X_train , X_test = df.loc[train_index,x_values], df.loc[test_index,x_values]
    y_train , y_test = df.loc[train_index,y_values].values.ravel(), df.loc[test_index,y_values]

    # Create the LightGBM data containers
    model.fit(X_train,y_train,eval_set=[(X_test,y_test),(X_train,y_train)],
          eval_metric='logloss')

    pred_values = model.predict(X_test)
     
    acc = accuracy_score(y_test, pred_values)
    acc_score.append(acc)
    
    Truth.extend(y_test.values.reshape(y_test.shape[0])); ## it is a list
    Output.extend(pred_values); ## it is a list  
    
    #print(model.feature_importances_)
#     Importance = pd.DataFrame({'Importance':(model.feature_importances_*100)}, 
#                           index = (X_train.columns))
#     Importance.sort_values(by = 'Importance', 
#                        axis = 0, 
#                        ascending = True).plot(kind = 'barh', 
#                                               color = 'r')
#     plt.xlabel('Variable Importance')
#     plt.gca().legend_ = None
    #plt.savefig('plot1.png')


elapsed = timeit.default_timer() - start_time #gives total computation time
print("---Run time is %s seconds ---" % elapsed) #prints computation time
print()

print('Accuracy of each fold: \n {}'.format(acc_score))
print()
print('Avg accuracy : \n{}'.format(np.mean(acc_score))); 
print()
print('Std of accuracy : \n{}'.format(np.std(acc_score)))

print(confusion_matrix(Truth, Output))
print(classification_report(Truth, Output))
print(acc_score)
print(elapsed)

[1]	training's binary_logloss: 0.625764	valid_0's binary_logloss: 0.566411
[2]	training's binary_logloss: 0.572388	valid_0's binary_logloss: 0.513349
[3]	training's binary_logloss: 0.528093	valid_0's binary_logloss: 0.469597
[4]	training's binary_logloss: 0.490921	valid_0's binary_logloss: 0.433164
[5]	training's binary_logloss: 0.459462	valid_0's binary_logloss: 0.402616
[6]	training's binary_logloss: 0.432653	valid_0's binary_logloss: 0.376693
[7]	training's binary_logloss: 0.409685	valid_0's binary_logloss: 0.354884
[8]	training's binary_logloss: 0.389927	valid_0's binary_logloss: 0.336377
[9]	training's binary_logloss: 0.372876	valid_0's binary_logloss: 0.320667
[10]	training's binary_logloss: 0.358117	valid_0's binary_logloss: 0.307304
[11]	training's binary_logloss: 0.345313	valid_0's binary_logloss: 0.295912
[12]	training's binary_logloss: 0.334178	valid_0's binary_logloss: 0.285994
[13]	training's binary_logloss: 0.324486	valid_0's binary_logloss: 0.277529
[14]	training's binar

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[92]	training's binary_logloss: 0.256555	valid_0's binary_logloss: 0.234746
[93]	training's binary_logloss: 0.256555	valid_0's binary_logloss: 0.23475
[94]	training's binary_logloss: 0.256555	valid_0's binary_logloss: 0.234753
[95]	training's binary_logloss: 0.256555	valid_0's binary_logloss: 0.234756
[96]	training's binary_logloss: 0.256555	valid_0's binary_logloss: 0.234758
[97]	training's binary_logloss: 0.256555	valid_0's binary_logloss: 0.23476
[98]	training's binary_logloss: 0.256555	valid_0's binary_logloss: 0.234762
[99]	training's binary_logloss: 0.256555	valid_0's binary_logloss: 0.234764
[100]	training's binary_logloss: 0.256555	valid_0's binary_logloss: 0.234765
[1]	training's binary_logloss: 0.62578	valid_0's binary_logloss: 0.590374
[2]	training's binary_logloss: 0.573019	valid_0's binary_logloss: 0.5361
[3]	training's binary_logloss: 0.529237	valid_0's binary_logloss: 0.490511
[4]	training's binary_logloss: 0.492504	valid_0's binary_logloss: 0.451756
[5]	training's binar

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[53]	training's binary_logloss: 0.260639	valid_0's binary_logloss: 0.18147
[54]	training's binary_logloss: 0.260584	valid_0's binary_logloss: 0.181374
[55]	training's binary_logloss: 0.260534	valid_0's binary_logloss: 0.18129
[56]	training's binary_logloss: 0.260491	valid_0's binary_logloss: 0.181217
[57]	training's binary_logloss: 0.260453	valid_0's binary_logloss: 0.181152
[58]	training's binary_logloss: 0.260419	valid_0's binary_logloss: 0.181101
[59]	training's binary_logloss: 0.260389	valid_0's binary_logloss: 0.181049
[60]	training's binary_logloss: 0.260363	valid_0's binary_logloss: 0.181003
[61]	training's binary_logloss: 0.26034	valid_0's binary_logloss: 0.180962
[62]	training's binary_logloss: 0.26032	valid_0's binary_logloss: 0.180927
[63]	training's binary_logloss: 0.260302	valid_0's binary_logloss: 0.180901
[64]	training's binary_logloss: 0.260287	valid_0's binary_logloss: 0.180874
[65]	training's binary_logloss: 0.260273	valid_0's binary_logloss: 0.180849
[66]	training's 

...

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.625489	valid_0's binary_logloss: 0.565302
[2]	training's binary_logloss: 0.572275	valid_0's binary_logloss: 0.510507
[3]	training's binary_logloss: 0.528116	valid_0's binary_logloss: 0.465099
[4]	training's binary_logloss: 0.491065	valid_0's binary_logloss: 0.427076
[5]	training's binary_logloss: 0.459703	valid_0's binary_logloss: 0.394829
[6]	training's binary_logloss: 0.432992	valid_0's binary_logloss: 0.367597
[7]	training's binary_logloss: 0.410104	valid_0's binary_logloss: 0.344205
[8]	training's binary_logloss: 0.39042	valid_0's binary_logloss: 0.324167
[9]	training's binary_logloss: 0.373436	valid_0's binary_logloss: 0.307134
[10]	training's binary_logloss: 0.358737	valid_0's binary_logloss: 0.2925
[11]	training's binary_logloss: 0.345988	valid_0's binary_logloss: 0.279911
[12]	training's binary_logloss: 0.334901	valid_0's binary_logloss: 0.268854
[13]	training's binary_logloss: 0.325251	valid_0's binary_logloss: 0.259311
[14]	training's binary_l

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.620778	valid_0's binary_logloss: 0.674549
[2]	training's binary_logloss: 0.56895	valid_0's binary_logloss: 0.598724
[3]	training's binary_logloss: 0.526008	valid_0's binary_logloss: 0.535638
[4]	training's binary_logloss: 0.490018	valid_0's binary_logloss: 0.482409
[5]	training's binary_logloss: 0.459596	valid_0's binary_logloss: 0.437357
[6]	training's binary_logloss: 0.43371	valid_0's binary_logloss: 0.398576
[7]	training's binary_logloss: 0.411546	valid_0's binary_logloss: 0.364747
[8]	training's binary_logloss: 0.392503	valid_0's binary_logloss: 0.335271
[9]	training's binary_logloss: 0.376084	valid_0's binary_logloss: 0.30946
[10]	training's binary_logloss: 0.361889	valid_0's binary_logloss: 0.286771
[11]	training's binary_logloss: 0.349581	valid_0's binary_logloss: 0.266701
[12]	training's binary_logloss: 0.338902	valid_0's binary_logloss: 0.248781
[13]	training's binary_logloss: 0.329617	valid_0's binary_logloss: 0.232896
[14]	training's binary_l

              precision    recall  f1-score   support

           0       0.91      0.85      0.88     24743
           1       0.83      0.90      0.87     20225

    accuracy                           0.88     44968
   macro avg       0.87      0.88      0.87     44968
weighted avg       0.88      0.88      0.88     44968

[0.8918764302059496, 0.9391480730223124, 0.993073047858942, 0.8165467625899281, 0.9848484848484849, 0.9079107505070994, 0.8748248482017749, 0.9625595643294759, 0.9061244979919679, 0.7502756339581036, 0.9777676950998185, 0.9425699928212491, 0.7519274376417233, 0.9796178343949045, 0.45087427144046627, 0.972972972972973, 0.9492803289924606, 0.93133294864397, 0.5287404902789519, 0.936778449697636, 0.9786142001710864, 0.9070935342121783, 0.9881606765327695]
5.480326400000003


In [12]:
# Regular to Long

import lightgbm

#Implementing cross validation 
#kf = KFold(n_splits=23, random_state=1, shuffle=True)
model = lightgbm.LGBMClassifier(learning_rate=0.1, n_estimators=100, max_depth=5, random_state=0)

from time import time
import timeit #imports timeit module
start_time = timeit.default_timer() #defines start time so computational time can be calculated

acc_score = [];
Truth = [];
Output = [];
n_estimators_list = []
max_depth_list = []

x_values = ['RtoL']
# 'StoS', 'StoR', 'StoL', 'RtoS', 'RtoR', 'RtoL', 'LtoS',
#        'LtoR', 'LtoL', 'STD', 'CoefVar', 'Range', 'Volatility', 'ShEn',
#        'AppEn', 'SampEn', 'IQR', 'Var', 'Rmean_Var', 'Mean_Absolute_Deviation'
y_values = ['Rhythm']
df = features_maindf

for idx, subject in enumerate(good_list):
    
    train_index = ~df['Subject'].str.contains(subject)
    test_index = df['Subject'].str.contains(subject)
    X_train , X_test = df.loc[train_index,x_values], df.loc[test_index,x_values]
    y_train , y_test = df.loc[train_index,y_values].values.ravel(), df.loc[test_index,y_values]

    # Create the LightGBM data containers
    model.fit(X_train,y_train,eval_set=[(X_test,y_test),(X_train,y_train)],
          eval_metric='logloss')

    pred_values = model.predict(X_test)
     
    acc = accuracy_score(y_test, pred_values)
    acc_score.append(acc)
    
    Truth.extend(y_test.values.reshape(y_test.shape[0])); ## it is a list
    Output.extend(pred_values); ## it is a list  
    
    #print(model.feature_importances_)
#     Importance = pd.DataFrame({'Importance':(model.feature_importances_*100)}, 
#                           index = (X_train.columns))
#     Importance.sort_values(by = 'Importance', 
#                        axis = 0, 
#                        ascending = True).plot(kind = 'barh', 
#                                               color = 'r')
#     plt.xlabel('Variable Importance')
#     plt.gca().legend_ = None
    #plt.savefig('plot1.png')


elapsed = timeit.default_timer() - start_time #gives total computation time
print("---Run time is %s seconds ---" % elapsed) #prints computation time
print()

print('Accuracy of each fold: \n {}'.format(acc_score))
print()
print('Avg accuracy : \n{}'.format(np.mean(acc_score))); 
print()
print('Std of accuracy : \n{}'.format(np.std(acc_score)))

print(confusion_matrix(Truth, Output))
print(classification_report(Truth, Output))
print(acc_score)
print(elapsed)

[1]	training's binary_logloss: 0.629008	valid_0's binary_logloss: 0.584412
[2]	training's binary_logloss: 0.578528	valid_0's binary_logloss: 0.545782
[3]	training's binary_logloss: 0.536884	valid_0's binary_logloss: 0.513962
[4]	training's binary_logloss: 0.50219	valid_0's binary_logloss: 0.487654
[5]	training's binary_logloss: 0.473071	valid_0's binary_logloss: 0.465867
[6]	training's binary_logloss: 0.448495	valid_0's binary_logloss: 0.447834
[7]	training's binary_logloss: 0.427666	valid_0's binary_logloss: 0.432945
[8]	training's binary_logloss: 0.409957	valid_0's binary_logloss: 0.420708
[9]	training's binary_logloss: 0.394862	valid_0's binary_logloss: 0.410721
[10]	training's binary_logloss: 0.381973	valid_0's binary_logloss: 0.402652
[11]	training's binary_logloss: 0.370954	valid_0's binary_logloss: 0.396223
[12]	training's binary_logloss: 0.361525	valid_0's binary_logloss: 0.391199
[13]	training's binary_logloss: 0.353452	valid_0's binary_logloss: 0.387381
[14]	training's binary

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.629118	valid_0's binary_logloss: 0.596705
[2]	training's binary_logloss: 0.579354	valid_0's binary_logloss: 0.547839
[3]	training's binary_logloss: 0.538331	valid_0's binary_logloss: 0.506901
[4]	training's binary_logloss: 0.504182	valid_0's binary_logloss: 0.472302
[5]	training's binary_logloss: 0.47555	valid_0's binary_logloss: 0.442859
[6]	training's binary_logloss: 0.451412	valid_0's binary_logloss: 0.417669
[7]	training's binary_logloss: 0.430982	valid_0's binary_logloss: 0.396026
[8]	training's binary_logloss: 0.413636	valid_0's binary_logloss: 0.377363
[9]	training's binary_logloss: 0.398876	valid_0's binary_logloss: 0.361226
[10]	training's binary_logloss: 0.386298	valid_0's binary_logloss: 0.347239
[11]	training's binary_logloss: 0.375566	valid_0's binary_logloss: 0.335092
[12]	training's binary_logloss: 0.366405	valid_0's binary_logloss: 0.324526
[13]	training's binary_logloss: 0.358583	valid_0's binary_logloss: 0.315321
[14]	training's binary

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.629777	valid_0's binary_logloss: 0.569407
[2]	training's binary_logloss: 0.580141	valid_0's binary_logloss: 0.519317
[3]	training's binary_logloss: 0.539215	valid_0's binary_logloss: 0.476732
[4]	training's binary_logloss: 0.505143	valid_0's binary_logloss: 0.440239
[5]	training's binary_logloss: 0.476575	valid_0's binary_logloss: 0.408765
[6]	training's binary_logloss: 0.452491	valid_0's binary_logloss: 0.381478
[7]	training's binary_logloss: 0.432107	valid_0's binary_logloss: 0.357718
[8]	training's binary_logloss: 0.414802	valid_0's binary_logloss: 0.336954
[9]	training's binary_logloss: 0.400079	valid_0's binary_logloss: 0.318751
[10]	training's binary_logloss: 0.387532	valid_0's binary_logloss: 0.302753
[11]	training's binary_logloss: 0.376829	valid_0's binary_logloss: 0.288661
[12]	training's binary_logloss: 0.367693	valid_0's binary_logloss: 0.276224
[13]	training's binary_logloss: 0.359893	valid_0's binary_logloss: 0.265228
[14]	training's binar

...

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.628518	valid_0's binary_logloss: 0.593849
[2]	training's binary_logloss: 0.578837	valid_0's binary_logloss: 0.543146
[3]	training's binary_logloss: 0.537898	valid_0's binary_logloss: 0.500533
[4]	training's binary_logloss: 0.503828	valid_0's binary_logloss: 0.46439
[5]	training's binary_logloss: 0.475267	valid_0's binary_logloss: 0.433515
[6]	training's binary_logloss: 0.451193	valid_0's binary_logloss: 0.406989
[7]	training's binary_logloss: 0.430819	valid_0's binary_logloss: 0.384095
[8]	training's binary_logloss: 0.413523	valid_0's binary_logloss: 0.364259
[9]	training's binary_logloss: 0.398807	valid_0's binary_logloss: 0.347019
[10]	training's binary_logloss: 0.386267	valid_0's binary_logloss: 0.331996
[11]	training's binary_logloss: 0.375569	valid_0's binary_logloss: 0.318873
[12]	training's binary_logloss: 0.366438	valid_0's binary_logloss: 0.307388
[13]	training's binary_logloss: 0.358641	valid_0's binary_logloss: 0.29732
[14]	training's binary_

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.629692	valid_0's binary_logloss: 0.57035
[2]	training's binary_logloss: 0.580167	valid_0's binary_logloss: 0.51822
[3]	training's binary_logloss: 0.539339	valid_0's binary_logloss: 0.473863
[4]	training's binary_logloss: 0.505353	valid_0's binary_logloss: 0.435804
[5]	training's binary_logloss: 0.476858	valid_0's binary_logloss: 0.402929
[6]	training's binary_logloss: 0.45284	valid_0's binary_logloss: 0.374377
[7]	training's binary_logloss: 0.432512	valid_0's binary_logloss: 0.349468
[8]	training's binary_logloss: 0.415256	valid_0's binary_logloss: 0.327654
[9]	training's binary_logloss: 0.400575	valid_0's binary_logloss: 0.30849
[10]	training's binary_logloss: 0.388066	valid_0's binary_logloss: 0.291608
[11]	training's binary_logloss: 0.377395	valid_0's binary_logloss: 0.276702
[12]	training's binary_logloss: 0.368288	valid_0's binary_logloss: 0.263514
[13]	training's binary_logloss: 0.360512	valid_0's binary_logloss: 0.251827
[14]	training's binary_lo

              precision    recall  f1-score   support

           0       0.89      0.94      0.91     24743
           1       0.92      0.86      0.89     20225

    accuracy                           0.90     44968
   macro avg       0.90      0.90      0.90     44968
weighted avg       0.90      0.90      0.90     44968

[0.8918764302059496, 0.9334685598377281, 0.9716624685138538, 0.8962829736211031, 0.9378265412748171, 0.954158215010142, 0.7949556282111163, 0.9639210347174949, 0.8744979919678715, 0.9388092613009923, 0.9224137931034483, 0.955491744436468, 0.8403628117913832, 0.943312101910828, 0.6144879267277269, 0.8985378821444395, 0.9561343385880741, 0.9388343912290825, 0.8423499577345731, 0.9477735019241341, 0.9396920444824637, 0.9824231010671689, 0.9424947145877378]
4.7270015


In [13]:
# Long to Short

import lightgbm

#Implementing cross validation 
#kf = KFold(n_splits=23, random_state=1, shuffle=True)
model = lightgbm.LGBMClassifier(learning_rate=0.1, n_estimators=100, max_depth=5, random_state=0)

from time import time
import timeit #imports timeit module
start_time = timeit.default_timer() #defines start time so computational time can be calculated

acc_score = [];
Truth = [];
Output = [];
n_estimators_list = []
max_depth_list = []

x_values = ['LtoS']
# 'StoS', 'StoR', 'StoL', 'RtoS', 'RtoR', 'RtoL', 'LtoS',
#        'LtoR', 'LtoL', 'STD', 'CoefVar', 'Range', 'Volatility', 'ShEn',
#        'AppEn', 'SampEn', 'IQR', 'Var', 'Rmean_Var', 'Mean_Absolute_Deviation'
y_values = ['Rhythm']
df = features_maindf

for idx, subject in enumerate(good_list):
    
    train_index = ~df['Subject'].str.contains(subject)
    test_index = df['Subject'].str.contains(subject)
    X_train , X_test = df.loc[train_index,x_values], df.loc[test_index,x_values]
    y_train , y_test = df.loc[train_index,y_values].values.ravel(), df.loc[test_index,y_values]

    # Create the LightGBM data containers
    model.fit(X_train,y_train,eval_set=[(X_test,y_test),(X_train,y_train)],
          eval_metric='logloss')

    pred_values = model.predict(X_test)
     
    acc = accuracy_score(y_test, pred_values)
    acc_score.append(acc)
    
    Truth.extend(y_test.values.reshape(y_test.shape[0])); ## it is a list
    Output.extend(pred_values); ## it is a list  
    
    #print(model.feature_importances_)
#     Importance = pd.DataFrame({'Importance':(model.feature_importances_*100)}, 
#                           index = (X_train.columns))
#     Importance.sort_values(by = 'Importance', 
#                        axis = 0, 
#                        ascending = True).plot(kind = 'barh', 
#                                               color = 'r')
#     plt.xlabel('Variable Importance')
#     plt.gca().legend_ = None
    #plt.savefig('plot1.png')


elapsed = timeit.default_timer() - start_time #gives total computation time
print("---Run time is %s seconds ---" % elapsed) #prints computation time
print()

print('Accuracy of each fold: \n {}'.format(acc_score))
print()
print('Avg accuracy : \n{}'.format(np.mean(acc_score))); 
print()
print('Std of accuracy : \n{}'.format(np.std(acc_score)))

print(confusion_matrix(Truth, Output))
print(classification_report(Truth, Output))
print(acc_score)
print(elapsed)

[1]	training's binary_logloss: 0.661233	valid_0's binary_logloss: 0.609662
[2]	training's binary_logloss: 0.637118	valid_0's binary_logloss: 0.591225
[3]	training's binary_logloss: 0.617367	valid_0's binary_logloss: 0.575746
[4]	training's binary_logloss: 0.601046	valid_0's binary_logloss: 0.562773
[5]	training's binary_logloss: 0.587471	valid_0's binary_logloss: 0.551932
[6]	training's binary_logloss: 0.576125	valid_0's binary_logloss: 0.542911
[7]	training's binary_logloss: 0.566603	valid_0's binary_logloss: 0.535447
[8]	training's binary_logloss: 0.558591	valid_0's binary_logloss: 0.529318
[9]	training's binary_logloss: 0.551834	valid_0's binary_logloss: 0.524332
[10]	training's binary_logloss: 0.546127	valid_0's binary_logloss: 0.520326
[11]	training's binary_logloss: 0.541299	valid_0's binary_logloss: 0.517159
[12]	training's binary_logloss: 0.537214	valid_0's binary_logloss: 0.514755
[13]	training's binary_logloss: 0.533756	valid_0's binary_logloss: 0.512907
[14]	training's binar

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)



[100]	training's binary_logloss: 0.515179	valid_0's binary_logloss: 0.526122
[1]	training's binary_logloss: 0.660801	valid_0's binary_logloss: 0.628788
[2]	training's binary_logloss: 0.636958	valid_0's binary_logloss: 0.60628
[3]	training's binary_logloss: 0.617455	valid_0's binary_logloss: 0.587309
[4]	training's binary_logloss: 0.601361	valid_0's binary_logloss: 0.571223
[5]	training's binary_logloss: 0.587994	valid_0's binary_logloss: 0.557521
[6]	training's binary_logloss: 0.576839	valid_0's binary_logloss: 0.545806
[7]	training's binary_logloss: 0.567489	valid_0's binary_logloss: 0.53575
[8]	training's binary_logloss: 0.559635	valid_0's binary_logloss: 0.527111
[9]	training's binary_logloss: 0.553023	valid_0's binary_logloss: 0.519677
[10]	training's binary_logloss: 0.547449	valid_0's binary_logloss: 0.513273
[11]	training's binary_logloss: 0.542744	valid_0's binary_logloss: 0.50775
[12]	training's binary_logloss: 0.538771	valid_0's binary_logloss: 0.502989
[13]	training's binary

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[68]	training's binary_logloss: 0.517711	valid_0's binary_logloss: 0.472354
[69]	training's binary_logloss: 0.517711	valid_0's binary_logloss: 0.472351
[70]	training's binary_logloss: 0.517711	valid_0's binary_logloss: 0.472347
[71]	training's binary_logloss: 0.517711	valid_0's binary_logloss: 0.472345
[72]	training's binary_logloss: 0.517711	valid_0's binary_logloss: 0.472342
[73]	training's binary_logloss: 0.517711	valid_0's binary_logloss: 0.47234
[74]	training's binary_logloss: 0.517711	valid_0's binary_logloss: 0.472338
[75]	training's binary_logloss: 0.517711	valid_0's binary_logloss: 0.472336
[76]	training's binary_logloss: 0.517711	valid_0's binary_logloss: 0.472334
[77]	training's binary_logloss: 0.517711	valid_0's binary_logloss: 0.472333
[78]	training's binary_logloss: 0.517711	valid_0's binary_logloss: 0.472331
[79]	training's binary_logloss: 0.517711	valid_0's binary_logloss: 0.47233
[80]	training's binary_logloss: 0.517711	valid_0's binary_logloss: 0.472329
[81]	training'

...

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.659951	valid_0's binary_logloss: 0.630136
[2]	training's binary_logloss: 0.635984	valid_0's binary_logloss: 0.609405
[3]	training's binary_logloss: 0.616393	valid_0's binary_logloss: 0.59191
[4]	training's binary_logloss: 0.600238	valid_0's binary_logloss: 0.57705
[5]	training's binary_logloss: 0.586828	valid_0's binary_logloss: 0.564364
[6]	training's binary_logloss: 0.575641	valid_0's binary_logloss: 0.553489
[7]	training's binary_logloss: 0.566273	valid_0's binary_logloss: 0.544136
[8]	training's binary_logloss: 0.558407	valid_0's binary_logloss: 0.536068
[9]	training's binary_logloss: 0.551788	valid_0's binary_logloss: 0.529091
[10]	training's binary_logloss: 0.546211	valid_0's binary_logloss: 0.523046
[11]	training's binary_logloss: 0.541507	valid_0's binary_logloss: 0.517797
[12]	training's binary_logloss: 0.537535	valid_0's binary_logloss: 0.513234
[13]	training's binary_logloss: 0.534183	valid_0's binary_logloss: 0.50926
[14]	training's binary_l

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.661173	valid_0's binary_logloss: 0.605265
[2]	training's binary_logloss: 0.637404	valid_0's binary_logloss: 0.582157
[3]	training's binary_logloss: 0.617952	valid_0's binary_logloss: 0.562296
[4]	training's binary_logloss: 0.601894	valid_0's binary_logloss: 0.545175
[5]	training's binary_logloss: 0.588553	valid_0's binary_logloss: 0.530381
[6]	training's binary_logloss: 0.577415	valid_0's binary_logloss: 0.517572
[7]	training's binary_logloss: 0.56808	valid_0's binary_logloss: 0.506478
[8]	training's binary_logloss: 0.560236	valid_0's binary_logloss: 0.496853
[9]	training's binary_logloss: 0.55363	valid_0's binary_logloss: 0.488503
[10]	training's binary_logloss: 0.548059	valid_0's binary_logloss: 0.481258
[11]	training's binary_logloss: 0.543355	valid_0's binary_logloss: 0.474973
[12]	training's binary_logloss: 0.539382	valid_0's binary_logloss: 0.469522
[13]	training's binary_logloss: 0.536025	valid_0's binary_logloss: 0.464798
[14]	training's binary_

              precision    recall  f1-score   support

           0       0.72      0.95      0.82     24743
           1       0.91      0.54      0.68     20225

    accuracy                           0.77     44968
   macro avg       0.81      0.75      0.75     44968
weighted avg       0.80      0.77      0.76     44968

[0.9136155606407322, 0.8543610547667343, 0.9848866498740554, 0.8890887290167866, 0.7826541274817137, 0.9379310344827586, 0.6562354040168146, 0.9863852961198094, 0.6154618473895582, 0.8798235942668137, 0.6710526315789473, 0.9454414931801867, 0.672108843537415, 0.7630573248407644, 0.14321398834304747, 0.6517501107665042, 0.9198080877313228, 0.6508944027697634, 0.8169907016060862, 0.8317757009345794, 0.7874251497005988, 0.9365976145637163, 0.7657505285412262]
4.656810700000001


In [14]:
# Long to Regular

import lightgbm

#Implementing cross validation 
#kf = KFold(n_splits=23, random_state=1, shuffle=True)
model = lightgbm.LGBMClassifier(learning_rate=0.1, n_estimators=100, max_depth=5, random_state=0)

from time import time
import timeit #imports timeit module
start_time = timeit.default_timer() #defines start time so computational time can be calculated

acc_score = [];
Truth = [];
Output = [];
n_estimators_list = []
max_depth_list = []

x_values = ['LtoR']
# 'StoS', 'StoR', 'StoL', 'RtoS', 'RtoR', 'RtoL', 'LtoS',
#        'LtoR', 'LtoL', 'STD', 'CoefVar', 'Range', 'Volatility', 'ShEn',
#        'AppEn', 'SampEn', 'IQR', 'Var', 'Rmean_Var', 'Mean_Absolute_Deviation'
y_values = ['Rhythm']
df = features_maindf

for idx, subject in enumerate(good_list):
    
    train_index = ~df['Subject'].str.contains(subject)
    test_index = df['Subject'].str.contains(subject)
    X_train , X_test = df.loc[train_index,x_values], df.loc[test_index,x_values]
    y_train , y_test = df.loc[train_index,y_values].values.ravel(), df.loc[test_index,y_values]

    # Create the LightGBM data containers
    model.fit(X_train,y_train,eval_set=[(X_test,y_test),(X_train,y_train)],
          eval_metric='logloss')

    pred_values = model.predict(X_test)
     
    acc = accuracy_score(y_test, pred_values)
    acc_score.append(acc)
    
    Truth.extend(y_test.values.reshape(y_test.shape[0])); ## it is a list
    Output.extend(pred_values); ## it is a list  
    
    #print(model.feature_importances_)
#     Importance = pd.DataFrame({'Importance':(model.feature_importances_*100)}, 
#                           index = (X_train.columns))
#     Importance.sort_values(by = 'Importance', 
#                        axis = 0, 
#                        ascending = True).plot(kind = 'barh', 
#                                               color = 'r')
#     plt.xlabel('Variable Importance')
#     plt.gca().legend_ = None
    #plt.savefig('plot1.png')


elapsed = timeit.default_timer() - start_time #gives total computation time
print("---Run time is %s seconds ---" % elapsed) #prints computation time
print()

print('Accuracy of each fold: \n {}'.format(acc_score))
print()
print('Avg accuracy : \n{}'.format(np.mean(acc_score))); 
print()
print('Std of accuracy : \n{}'.format(np.std(acc_score)))

print(confusion_matrix(Truth, Output))
print(classification_report(Truth, Output))
print(acc_score)
print(elapsed)

[1]	training's binary_logloss: 0.650132	valid_0's binary_logloss: 0.586046
[2]	training's binary_logloss: 0.616831	valid_0's binary_logloss: 0.548093
[3]	training's binary_logloss: 0.589481	valid_0's binary_logloss: 0.516197
[4]	training's binary_logloss: 0.566878	valid_0's binary_logloss: 0.489197
[5]	training's binary_logloss: 0.548112	valid_0's binary_logloss: 0.46621
[6]	training's binary_logloss: 0.532482	valid_0's binary_logloss: 0.446546
[7]	training's binary_logloss: 0.519435	valid_0's binary_logloss: 0.429657
[8]	training's binary_logloss: 0.508528	valid_0's binary_logloss: 0.415103
[9]	training's binary_logloss: 0.499403	valid_0's binary_logloss: 0.402523
[10]	training's binary_logloss: 0.491768	valid_0's binary_logloss: 0.391624
[11]	training's binary_logloss: 0.485379	valid_0's binary_logloss: 0.382159
[12]	training's binary_logloss: 0.480036	valid_0's binary_logloss: 0.373923
[13]	training's binary_logloss: 0.475571	valid_0's binary_logloss: 0.366743
[14]	training's binary

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.650133	valid_0's binary_logloss: 0.604915
[2]	training's binary_logloss: 0.617429	valid_0's binary_logloss: 0.562387
[3]	training's binary_logloss: 0.590575	valid_0's binary_logloss: 0.526443
[4]	training's binary_logloss: 0.568387	valid_0's binary_logloss: 0.495835
[5]	training's binary_logloss: 0.549971	valid_0's binary_logloss: 0.469611
[6]	training's binary_logloss: 0.534636	valid_0's binary_logloss: 0.447033
[7]	training's binary_logloss: 0.521841	valid_0's binary_logloss: 0.427512
[8]	training's binary_logloss: 0.511148	valid_0's binary_logloss: 0.410576
[9]	training's binary_logloss: 0.502206	valid_0's binary_logloss: 0.395839
[10]	training's binary_logloss: 0.494726	valid_0's binary_logloss: 0.382982
[11]	training's binary_logloss: 0.48847	valid_0's binary_logloss: 0.371741
[12]	training's binary_logloss: 0.48324	valid_0's binary_logloss: 0.361892
[13]	training's binary_logloss: 0.478871	valid_0's binary_logloss: 0.353248
[14]	training's binary_

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.650193	valid_0's binary_logloss: 0.578732
[2]	training's binary_logloss: 0.617147	valid_0's binary_logloss: 0.536523
[3]	training's binary_logloss: 0.59001	valid_0's binary_logloss: 0.500683
[4]	training's binary_logloss: 0.567587	valid_0's binary_logloss: 0.470017
[5]	training's binary_logloss: 0.548975	valid_0's binary_logloss: 0.44361
[6]	training's binary_logloss: 0.533477	valid_0's binary_logloss: 0.420752
[7]	training's binary_logloss: 0.520544	valid_0's binary_logloss: 0.400876
[8]	training's binary_logloss: 0.509736	valid_0's binary_logloss: 0.383527
[9]	training's binary_logloss: 0.500697	valid_0's binary_logloss: 0.368334
[10]	training's binary_logloss: 0.493136	valid_0's binary_logloss: 0.354991
[11]	training's binary_logloss: 0.486811	valid_0's binary_logloss: 0.343242
[12]	training's binary_logloss: 0.481524	valid_0's binary_logloss: 0.332874
[13]	training's binary_logloss: 0.477107	valid_0's binary_logloss: 0.323707
[14]	training's binary_

...

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.649568	valid_0's binary_logloss: 0.588353
[2]	training's binary_logloss: 0.616188	valid_0's binary_logloss: 0.551848
[3]	training's binary_logloss: 0.588774	valid_0's binary_logloss: 0.521234
[4]	training's binary_logloss: 0.566118	valid_0's binary_logloss: 0.495381
[5]	training's binary_logloss: 0.547308	valid_0's binary_logloss: 0.473426
[6]	training's binary_logloss: 0.53164	valid_0's binary_logloss: 0.454698
[7]	training's binary_logloss: 0.51856	valid_0's binary_logloss: 0.438661
[8]	training's binary_logloss: 0.507626	valid_0's binary_logloss: 0.424885
[9]	training's binary_logloss: 0.498478	valid_0's binary_logloss: 0.413021
[10]	training's binary_logloss: 0.490822	valid_0's binary_logloss: 0.402778
[11]	training's binary_logloss: 0.484416	valid_0's binary_logloss: 0.393918
[12]	training's binary_logloss: 0.479058	valid_0's binary_logloss: 0.386239
[13]	training's binary_logloss: 0.474581	valid_0's binary_logloss: 0.379574
[14]	training's binary_

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.643808	valid_0's binary_logloss: 0.712421
[2]	training's binary_logloss: 0.610914	valid_0's binary_logloss: 0.667931
[3]	training's binary_logloss: 0.583935	valid_0's binary_logloss: 0.63099
[4]	training's binary_logloss: 0.56166	valid_0's binary_logloss: 0.600037
[5]	training's binary_logloss: 0.543179	valid_0's binary_logloss: 0.57392
[6]	training's binary_logloss: 0.527795	valid_0's binary_logloss: 0.551762
[7]	training's binary_logloss: 0.514958	valid_0's binary_logloss: 0.532882
[8]	training's binary_logloss: 0.504231	valid_0's binary_logloss: 0.516737
[9]	training's binary_logloss: 0.495259	valid_0's binary_logloss: 0.502891
[10]	training's binary_logloss: 0.487753	valid_0's binary_logloss: 0.490989
[11]	training's binary_logloss: 0.481474	valid_0's binary_logloss: 0.480737
[12]	training's binary_logloss: 0.476223	valid_0's binary_logloss: 0.47189
[13]	training's binary_logloss: 0.471836	valid_0's binary_logloss: 0.464244
[14]	training's binary_lo

              precision    recall  f1-score   support

           0       0.87      0.79      0.83     24743
           1       0.77      0.86      0.81     20225

    accuracy                           0.82     44968
   macro avg       0.82      0.82      0.82     44968
weighted avg       0.83      0.82      0.82     44968

[0.8718535469107551, 0.918052738336714, 0.9074307304785895, 0.6786570743405276, 0.8766980146290491, 0.8945233265720081, 0.8187762727697337, 0.9196732471068755, 0.7911646586345381, 0.6119073869900772, 0.9065335753176044, 0.7616654702081838, 0.7705215419501134, 0.9363057324840764, 0.6369691923397169, 0.9091714665485158, 0.7950651130911583, 0.8926716676283901, 0.46956889264581575, 0.9054425508521166, 0.9067579127459366, 0.8593848085373509, 0.8862579281183932]
5.068821200000002


In [15]:
# Long to Long

import lightgbm

#Implementing cross validation 
#kf = KFold(n_splits=23, random_state=1, shuffle=True)
model = lightgbm.LGBMClassifier(learning_rate=0.1, n_estimators=100, max_depth=5, random_state=0)

from time import time
import timeit #imports timeit module
start_time = timeit.default_timer() #defines start time so computational time can be calculated

acc_score = [];
Truth = [];
Output = [];
n_estimators_list = []
max_depth_list = []

x_values = ['LtoL']
# 'StoS', 'StoR', 'StoL', 'RtoS', 'RtoR', 'RtoL', 'LtoS',
#        'LtoR', 'LtoL', 'STD', 'CoefVar', 'Range', 'Volatility', 'ShEn',
#        'AppEn', 'SampEn', 'IQR', 'Var', 'Rmean_Var', 'Mean_Absolute_Deviation'
y_values = ['Rhythm']
df = features_maindf

for idx, subject in enumerate(good_list):
    
    train_index = ~df['Subject'].str.contains(subject)
    test_index = df['Subject'].str.contains(subject)
    X_train , X_test = df.loc[train_index,x_values], df.loc[test_index,x_values]
    y_train , y_test = df.loc[train_index,y_values].values.ravel(), df.loc[test_index,y_values]

    # Create the LightGBM data containers
    model.fit(X_train,y_train,eval_set=[(X_test,y_test),(X_train,y_train)],
          eval_metric='logloss')

    pred_values = model.predict(X_test)
     
    acc = accuracy_score(y_test, pred_values)
    acc_score.append(acc)
    
    Truth.extend(y_test.values.reshape(y_test.shape[0])); ## it is a list
    Output.extend(pred_values); ## it is a list  
    
    #print(model.feature_importances_)
#     Importance = pd.DataFrame({'Importance':(model.feature_importances_*100)}, 
#                           index = (X_train.columns))
#     Importance.sort_values(by = 'Importance', 
#                        axis = 0, 
#                        ascending = True).plot(kind = 'barh', 
#                                               color = 'r')
#     plt.xlabel('Variable Importance')
#     plt.gca().legend_ = None
    #plt.savefig('plot1.png')


elapsed = timeit.default_timer() - start_time #gives total computation time
print("---Run time is %s seconds ---" % elapsed) #prints computation time
print()

print('Accuracy of each fold: \n {}'.format(acc_score))
print()
print('Avg accuracy : \n{}'.format(np.mean(acc_score))); 
print()
print('Std of accuracy : \n{}'.format(np.std(acc_score)))

print(confusion_matrix(Truth, Output))
print(classification_report(Truth, Output))
print(acc_score)
print(elapsed)

[1]	training's binary_logloss: 0.677383	valid_0's binary_logloss: 0.622855
[2]	training's binary_logloss: 0.666358	valid_0's binary_logloss: 0.615579
[3]	training's binary_logloss: 0.657343	valid_0's binary_logloss: 0.609579
[4]	training's binary_logloss: 0.649903	valid_0's binary_logloss: 0.604678
[5]	training's binary_logloss: 0.643722	valid_0's binary_logloss: 0.600725
[6]	training's binary_logloss: 0.638559	valid_0's binary_logloss: 0.597587
[7]	training's binary_logloss: 0.634232	valid_0's binary_logloss: 0.595148
[8]	training's binary_logloss: 0.630594	valid_0's binary_logloss: 0.593307
[9]	training's binary_logloss: 0.627529	valid_0's binary_logloss: 0.591976
[10]	training's binary_logloss: 0.624945	valid_0's binary_logloss: 0.591077
[11]	training's binary_logloss: 0.622763	valid_0's binary_logloss: 0.590543
[12]	training's binary_logloss: 0.62092	valid_0's binary_logloss: 0.590312
[13]	training's binary_logloss: 0.619364	valid_0's binary_logloss: 0.590333
[14]	training's binary

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[82]	training's binary_logloss: 0.611255	valid_0's binary_logloss: 0.607766
[83]	training's binary_logloss: 0.611255	valid_0's binary_logloss: 0.607769
[84]	training's binary_logloss: 0.611255	valid_0's binary_logloss: 0.607772
[85]	training's binary_logloss: 0.611255	valid_0's binary_logloss: 0.607775
[86]	training's binary_logloss: 0.611255	valid_0's binary_logloss: 0.607777
[87]	training's binary_logloss: 0.611255	valid_0's binary_logloss: 0.607779
[88]	training's binary_logloss: 0.611255	valid_0's binary_logloss: 0.607781
[89]	training's binary_logloss: 0.611255	valid_0's binary_logloss: 0.607783
[90]	training's binary_logloss: 0.611255	valid_0's binary_logloss: 0.607784
[91]	training's binary_logloss: 0.611255	valid_0's binary_logloss: 0.607786
[92]	training's binary_logloss: 0.611255	valid_0's binary_logloss: 0.607787
[93]	training's binary_logloss: 0.611255	valid_0's binary_logloss: 0.607788
[94]	training's binary_logloss: 0.611255	valid_0's binary_logloss: 0.607789
[95]	trainin

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[46]	training's binary_logloss: 0.612825	valid_0's binary_logloss: 0.57433
[47]	training's binary_logloss: 0.612823	valid_0's binary_logloss: 0.574306
[48]	training's binary_logloss: 0.612821	valid_0's binary_logloss: 0.574285
[49]	training's binary_logloss: 0.612819	valid_0's binary_logloss: 0.574265
[50]	training's binary_logloss: 0.612818	valid_0's binary_logloss: 0.574248
[51]	training's binary_logloss: 0.612817	valid_0's binary_logloss: 0.574233
[52]	training's binary_logloss: 0.612817	valid_0's binary_logloss: 0.574219
[53]	training's binary_logloss: 0.612816	valid_0's binary_logloss: 0.574207
[54]	training's binary_logloss: 0.612816	valid_0's binary_logloss: 0.574196
[55]	training's binary_logloss: 0.612815	valid_0's binary_logloss: 0.574186
[56]	training's binary_logloss: 0.612815	valid_0's binary_logloss: 0.574177
[57]	training's binary_logloss: 0.612815	valid_0's binary_logloss: 0.574169
[58]	training's binary_logloss: 0.612814	valid_0's binary_logloss: 0.574162
[59]	training

...

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.677286	valid_0's binary_logloss: 0.619556
[2]	training's binary_logloss: 0.666568	valid_0's binary_logloss: 0.608507
[3]	training's binary_logloss: 0.657816	valid_0's binary_logloss: 0.59888
[4]	training's binary_logloss: 0.650605	valid_0's binary_logloss: 0.59048
[5]	training's binary_logloss: 0.644625	valid_0's binary_logloss: 0.583142
[6]	training's binary_logloss: 0.639641	valid_0's binary_logloss: 0.576728
[7]	training's binary_logloss: 0.635472	valid_0's binary_logloss: 0.571118
[8]	training's binary_logloss: 0.631976	valid_0's binary_logloss: 0.56621
[9]	training's binary_logloss: 0.629039	valid_0's binary_logloss: 0.561917
[10]	training's binary_logloss: 0.626567	valid_0's binary_logloss: 0.558162
[11]	training's binary_logloss: 0.624487	valid_0's binary_logloss: 0.554877
[12]	training's binary_logloss: 0.622735	valid_0's binary_logloss: 0.552006
[13]	training's binary_logloss: 0.62126	valid_0's binary_logloss: 0.549495
[14]	training's binary_lo

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.671219	valid_0's binary_logloss: 0.741803
[2]	training's binary_logloss: 0.660781	valid_0's binary_logloss: 0.722065
[3]	training's binary_logloss: 0.652324	valid_0's binary_logloss: 0.706077
[4]	training's binary_logloss: 0.6454	valid_0's binary_logloss: 0.692928
[5]	training's binary_logloss: 0.639689	valid_0's binary_logloss: 0.681986
[6]	training's binary_logloss: 0.634952	valid_0's binary_logloss: 0.67279
[7]	training's binary_logloss: 0.631007	valid_0's binary_logloss: 0.664999
[8]	training's binary_logloss: 0.627711	valid_0's binary_logloss: 0.658352
[9]	training's binary_logloss: 0.624953	valid_0's binary_logloss: 0.652647
[10]	training's binary_logloss: 0.622641	valid_0's binary_logloss: 0.647725
[11]	training's binary_logloss: 0.620701	valid_0's binary_logloss: 0.64346
[12]	training's binary_logloss: 0.619073	valid_0's binary_logloss: 0.639747
[13]	training's binary_logloss: 0.617707	valid_0's binary_logloss: 0.636506
[14]	training's binary_lo

              precision    recall  f1-score   support

           0       0.63      0.97      0.76     24743
           1       0.89      0.31      0.46     20225

    accuracy                           0.67     44968
   macro avg       0.76      0.64      0.61     44968
weighted avg       0.75      0.67      0.63     44968

[0.9262013729977117, 0.8020283975659229, 0.9842569269521411, 0.8099520383693045, 0.5501567398119123, 0.9156186612576065, 0.5035030359645025, 0.9768550034036759, 0.4643574297188755, 0.9448732083792724, 0.39655172413793105, 0.9842067480258435, 0.6408163265306123, 0.47579617834394905, 0.02289758534554538, 0.461674789543642, 0.8773132282385195, 0.5164454702827467, 0.7852916314454776, 0.7927432655305112, 0.5945252352437981, 0.9353421217827997, 0.5577167019027485]
4.96479029999999


In [16]:
# Standard Deviation

import lightgbm

#Implementing cross validation 
#kf = KFold(n_splits=23, random_state=1, shuffle=True)
model = lightgbm.LGBMClassifier(learning_rate=0.1, n_estimators=100, max_depth=5, random_state=0)

from time import time
import timeit #imports timeit module
start_time = timeit.default_timer() #defines start time so computational time can be calculated

acc_score = [];
Truth = [];
Output = [];
n_estimators_list = []
max_depth_list = []

x_values = ['STD']
# 'StoS', 'StoR', 'StoL', 'RtoS', 'RtoR', 'RtoL', 'LtoS',
#        'LtoR', 'LtoL', 'STD', 'CoefVar', 'Range', 'Volatility', 'ShEn',
#        'AppEn', 'SampEn', 'IQR', 'Var', 'Rmean_Var', 'Mean_Absolute_Deviation'
y_values = ['Rhythm']
df = features_maindf

for idx, subject in enumerate(good_list):
    
    train_index = ~df['Subject'].str.contains(subject)
    test_index = df['Subject'].str.contains(subject)
    X_train , X_test = df.loc[train_index,x_values], df.loc[test_index,x_values]
    y_train , y_test = df.loc[train_index,y_values].values.ravel(), df.loc[test_index,y_values]

    # Create the LightGBM data containers
    model.fit(X_train,y_train,eval_set=[(X_test,y_test),(X_train,y_train)],
          eval_metric='logloss')

    pred_values = model.predict(X_test)
     
    acc = accuracy_score(y_test, pred_values)
    acc_score.append(acc)
    
    Truth.extend(y_test.values.reshape(y_test.shape[0])); ## it is a list
    Output.extend(pred_values); ## it is a list  
    
    #print(model.feature_importances_)
#     Importance = pd.DataFrame({'Importance':(model.feature_importances_*100)}, 
#                           index = (X_train.columns))
#     Importance.sort_values(by = 'Importance', 
#                        axis = 0, 
#                        ascending = True).plot(kind = 'barh', 
#                                               color = 'r')
#     plt.xlabel('Variable Importance')
#     plt.gca().legend_ = None
    #plt.savefig('plot1.png')


elapsed = timeit.default_timer() - start_time #gives total computation time
print("---Run time is %s seconds ---" % elapsed) #prints computation time
print()

print('Accuracy of each fold: \n {}'.format(acc_score))
print()
print('Avg accuracy : \n{}'.format(np.mean(acc_score))); 
print()
print('Std of accuracy : \n{}'.format(np.std(acc_score)))

print(confusion_matrix(Truth, Output))
print(classification_report(Truth, Output))
print(acc_score)
print(elapsed)

[1]	training's binary_logloss: 0.640588	valid_0's binary_logloss: 0.577308
[2]	training's binary_logloss: 0.59923	valid_0's binary_logloss: 0.533496
[3]	training's binary_logloss: 0.564914	valid_0's binary_logloss: 0.497672
[4]	training's binary_logloss: 0.536151	valid_0's binary_logloss: 0.468097
[5]	training's binary_logloss: 0.511862	valid_0's binary_logloss: 0.443469
[6]	training's binary_logloss: 0.49122	valid_0's binary_logloss: 0.422874
[7]	training's binary_logloss: 0.473576	valid_0's binary_logloss: 0.405538
[8]	training's binary_logloss: 0.458445	valid_0's binary_logloss: 0.390911
[9]	training's binary_logloss: 0.445423	valid_0's binary_logloss: 0.378525
[10]	training's binary_logloss: 0.434182	valid_0's binary_logloss: 0.367965
[11]	training's binary_logloss: 0.424459	valid_0's binary_logloss: 0.359039
[12]	training's binary_logloss: 0.416029	valid_0's binary_logloss: 0.35141
[13]	training's binary_logloss: 0.408706	valid_0's binary_logloss: 0.344938
[14]	training's binary_l

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[53]	training's binary_logloss: 0.357909	valid_0's binary_logloss: 0.305424
[54]	training's binary_logloss: 0.357856	valid_0's binary_logloss: 0.30539
[55]	training's binary_logloss: 0.35782	valid_0's binary_logloss: 0.305328
[56]	training's binary_logloss: 0.35779	valid_0's binary_logloss: 0.305297
[57]	training's binary_logloss: 0.357766	valid_0's binary_logloss: 0.305228
[58]	training's binary_logloss: 0.35773	valid_0's binary_logloss: 0.305199
[59]	training's binary_logloss: 0.3577	valid_0's binary_logloss: 0.305199
[60]	training's binary_logloss: 0.357668	valid_0's binary_logloss: 0.30516
[61]	training's binary_logloss: 0.357637	valid_0's binary_logloss: 0.305203
[62]	training's binary_logloss: 0.357615	valid_0's binary_logloss: 0.305158
[63]	training's binary_logloss: 0.357582	valid_0's binary_logloss: 0.305158
[64]	training's binary_logloss: 0.357553	valid_0's binary_logloss: 0.305137
[65]	training's binary_logloss: 0.357527	valid_0's binary_logloss: 0.305123
[66]	training's bin

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[2]	training's binary_logloss: 0.600687	valid_0's binary_logloss: 0.53891
[3]	training's binary_logloss: 0.567209	valid_0's binary_logloss: 0.494427
[4]	training's binary_logloss: 0.539119	valid_0's binary_logloss: 0.456775
[5]	training's binary_logloss: 0.515396	valid_0's binary_logloss: 0.424567
[6]	training's binary_logloss: 0.495217	valid_0's binary_logloss: 0.396829
[7]	training's binary_logloss: 0.477985	valid_0's binary_logloss: 0.372813
[8]	training's binary_logloss: 0.463207	valid_0's binary_logloss: 0.351971
[9]	training's binary_logloss: 0.450492	valid_0's binary_logloss: 0.333723
[10]	training's binary_logloss: 0.439518	valid_0's binary_logloss: 0.31777
[11]	training's binary_logloss: 0.430021	valid_0's binary_logloss: 0.303737
[12]	training's binary_logloss: 0.421792	valid_0's binary_logloss: 0.291378
[13]	training's binary_logloss: 0.414635	valid_0's binary_logloss: 0.280545
[14]	training's binary_logloss: 0.408411	valid_0's binary_logloss: 0.270977
[15]	training's binary

...

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.640272	valid_0's binary_logloss: 0.578656
[2]	training's binary_logloss: 0.599068	valid_0's binary_logloss: 0.534789
[3]	training's binary_logloss: 0.564875	valid_0's binary_logloss: 0.498982
[4]	training's binary_logloss: 0.536217	valid_0's binary_logloss: 0.468893
[5]	training's binary_logloss: 0.511983	valid_0's binary_logloss: 0.44371
[6]	training's binary_logloss: 0.491387	valid_0's binary_logloss: 0.4225
[7]	training's binary_logloss: 0.473797	valid_0's binary_logloss: 0.404488
[8]	training's binary_logloss: 0.458707	valid_0's binary_logloss: 0.389093
[9]	training's binary_logloss: 0.445722	valid_0's binary_logloss: 0.375938
[10]	training's binary_logloss: 0.434516	valid_0's binary_logloss: 0.364657
[11]	training's binary_logloss: 0.424814	valid_0's binary_logloss: 0.354977
[12]	training's binary_logloss: 0.416411	valid_0's binary_logloss: 0.346629
[13]	training's binary_logloss: 0.409107	valid_0's binary_logloss: 0.33944
[14]	training's binary_lo

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.63537	valid_0's binary_logloss: 0.699422
[2]	training's binary_logloss: 0.595283	valid_0's binary_logloss: 0.643773
[3]	training's binary_logloss: 0.561972	valid_0's binary_logloss: 0.596801
[4]	training's binary_logloss: 0.534056	valid_0's binary_logloss: 0.556827
[5]	training's binary_logloss: 0.510483	valid_0's binary_logloss: 0.522497
[6]	training's binary_logloss: 0.490453	valid_0's binary_logloss: 0.492848
[7]	training's binary_logloss: 0.47333	valid_0's binary_logloss: 0.46694
[8]	training's binary_logloss: 0.45864	valid_0's binary_logloss: 0.444392
[9]	training's binary_logloss: 0.44601	valid_0's binary_logloss: 0.424536
[10]	training's binary_logloss: 0.435103	valid_0's binary_logloss: 0.407096
[11]	training's binary_logloss: 0.425677	valid_0's binary_logloss: 0.391662
[12]	training's binary_logloss: 0.417499	valid_0's binary_logloss: 0.378028
[13]	training's binary_logloss: 0.410399	valid_0's binary_logloss: 0.365933
[14]	training's binary_log

              precision    recall  f1-score   support

           0       0.87      0.71      0.78     24743
           1       0.71      0.87      0.78     20225

    accuracy                           0.78     44968
   macro avg       0.79      0.79      0.78     44968
weighted avg       0.80      0.78      0.78     44968

[0.8043478260869565, 0.9237322515212981, 0.8835012594458438, 0.40707434052757796, 0.9164054336468129, 0.8993914807302231, 0.9098552078468005, 0.8781484002722941, 0.8519076305220884, 0.5705622932745315, 0.9736842105263158, 0.7336683417085427, 0.6276643990929706, 0.7923566878980892, 0.2231473771856786, 0.8825875055383252, 0.7971213159698424, 0.9359492210040392, 0.4429416737109045, 0.8911489829576691, 0.9461077844311377, 0.8261142498430634, 0.9357293868921776]
5.978767500000004


In [17]:
# Coefficient of Variance

import lightgbm

#Implementing cross validation 
#kf = KFold(n_splits=23, random_state=1, shuffle=True)
model = lightgbm.LGBMClassifier(learning_rate=0.1, n_estimators=100, max_depth=5, random_state=0)

from time import time
import timeit #imports timeit module
start_time = timeit.default_timer() #defines start time so computational time can be calculated

acc_score = [];
Truth = [];
Output = [];
n_estimators_list = []
max_depth_list = []

x_values = ['CoefVar']
# 'StoS', 'StoR', 'StoL', 'RtoS', 'RtoR', 'RtoL', 'LtoS',
#        'LtoR', 'LtoL', 'STD', 'CoefVar', 'Range', 'Volatility', 'ShEn',
#        'AppEn', 'SampEn', 'IQR', 'Var', 'Rmean_Var', 'Mean_Absolute_Deviation'
y_values = ['Rhythm']
df = features_maindf

for idx, subject in enumerate(good_list):
    
    train_index = ~df['Subject'].str.contains(subject)
    test_index = df['Subject'].str.contains(subject)
    X_train , X_test = df.loc[train_index,x_values], df.loc[test_index,x_values]
    y_train , y_test = df.loc[train_index,y_values].values.ravel(), df.loc[test_index,y_values]

    # Create the LightGBM data containers
    model.fit(X_train,y_train,eval_set=[(X_test,y_test),(X_train,y_train)],
          eval_metric='logloss')

    pred_values = model.predict(X_test)
     
    acc = accuracy_score(y_test, pred_values)
    acc_score.append(acc)
    
    Truth.extend(y_test.values.reshape(y_test.shape[0])); ## it is a list
    Output.extend(pred_values); ## it is a list  
    
    #print(model.feature_importances_)
#     Importance = pd.DataFrame({'Importance':(model.feature_importances_*100)}, 
#                           index = (X_train.columns))
#     Importance.sort_values(by = 'Importance', 
#                        axis = 0, 
#                        ascending = True).plot(kind = 'barh', 
#                                               color = 'r')
#     plt.xlabel('Variable Importance')
#     plt.gca().legend_ = None
    #plt.savefig('plot1.png')


elapsed = timeit.default_timer() - start_time #gives total computation time
print("---Run time is %s seconds ---" % elapsed) #prints computation time
print()

print('Accuracy of each fold: \n {}'.format(acc_score))
print()
print('Avg accuracy : \n{}'.format(np.mean(acc_score))); 
print()
print('Std of accuracy : \n{}'.format(np.std(acc_score)))

print(confusion_matrix(Truth, Output))
print(classification_report(Truth, Output))
print(acc_score)
print(elapsed)

[1]	training's binary_logloss: 0.632196	valid_0's binary_logloss: 0.572445
[2]	training's binary_logloss: 0.584047	valid_0's binary_logloss: 0.524275
[3]	training's binary_logloss: 0.544102	valid_0's binary_logloss: 0.484642
[4]	training's binary_logloss: 0.510608	valid_0's binary_logloss: 0.451673
[5]	training's binary_logloss: 0.48229	valid_0's binary_logloss: 0.423938
[6]	training's binary_logloss: 0.458199	valid_0's binary_logloss: 0.400502
[7]	training's binary_logloss: 0.437596	valid_0's binary_logloss: 0.38065
[8]	training's binary_logloss: 0.419905	valid_0's binary_logloss: 0.363766
[9]	training's binary_logloss: 0.404655	valid_0's binary_logloss: 0.349427
[10]	training's binary_logloss: 0.391477	valid_0's binary_logloss: 0.337159
[11]	training's binary_logloss: 0.380061	valid_0's binary_logloss: 0.326664
[12]	training's binary_logloss: 0.370162	valid_0's binary_logloss: 0.317608
[13]	training's binary_logloss: 0.361555	valid_0's binary_logloss: 0.309853
[14]	training's binary_

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[64]	training's binary_logloss: 0.300933	valid_0's binary_logloss: 0.259783
[65]	training's binary_logloss: 0.300913	valid_0's binary_logloss: 0.259778
[66]	training's binary_logloss: 0.300891	valid_0's binary_logloss: 0.259783
[67]	training's binary_logloss: 0.300868	valid_0's binary_logloss: 0.259742
[68]	training's binary_logloss: 0.300841	valid_0's binary_logloss: 0.259682
[69]	training's binary_logloss: 0.300821	valid_0's binary_logloss: 0.259757
[70]	training's binary_logloss: 0.300801	valid_0's binary_logloss: 0.259774
[71]	training's binary_logloss: 0.300778	valid_0's binary_logloss: 0.259693
[72]	training's binary_logloss: 0.300762	valid_0's binary_logloss: 0.259644
[73]	training's binary_logloss: 0.300747	valid_0's binary_logloss: 0.259683
[74]	training's binary_logloss: 0.300731	valid_0's binary_logloss: 0.259628
[75]	training's binary_logloss: 0.300716	valid_0's binary_logloss: 0.259691
[76]	training's binary_logloss: 0.300701	valid_0's binary_logloss: 0.259701
[77]	trainin

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[9]	training's binary_logloss: 0.408666	valid_0's binary_logloss: 0.309584
[10]	training's binary_logloss: 0.395724	valid_0's binary_logloss: 0.292832
[11]	training's binary_logloss: 0.38452	valid_0's binary_logloss: 0.278186
[12]	training's binary_logloss: 0.374802	valid_0's binary_logloss: 0.265341
[13]	training's binary_logloss: 0.366356	valid_0's binary_logloss: 0.254083
[14]	training's binary_logloss: 0.359002	valid_0's binary_logloss: 0.244181
[15]	training's binary_logloss: 0.352592	valid_0's binary_logloss: 0.23545
[16]	training's binary_logloss: 0.347001	valid_0's binary_logloss: 0.227758
[17]	training's binary_logloss: 0.342119	valid_0's binary_logloss: 0.220975
[18]	training's binary_logloss: 0.337853	valid_0's binary_logloss: 0.214983
[19]	training's binary_logloss: 0.334123	valid_0's binary_logloss: 0.209689
[20]	training's binary_logloss: 0.330856	valid_0's binary_logloss: 0.205013
[21]	training's binary_logloss: 0.327995	valid_0's binary_logloss: 0.200898
[22]	training's

...

[1]	training's binary_logloss: 0.626855	valid_0's binary_logloss: 0.693257
[2]	training's binary_logloss: 0.580166	valid_0's binary_logloss: 0.625135
[3]	training's binary_logloss: 0.541438	valid_0's binary_logloss: 0.568795
[4]	training's binary_logloss: 0.508979	valid_0's binary_logloss: 0.521794
[5]	training's binary_logloss: 0.481561	valid_0's binary_logloss: 0.481865
[6]	training's binary_logloss: 0.45826	valid_0's binary_logloss: 0.446672
[7]	training's binary_logloss: 0.438328	valid_0's binary_logloss: 0.416966
[8]	training's binary_logloss: 0.421223	valid_0's binary_logloss: 0.391017
[9]	training's binary_logloss: 0.406492	valid_0's binary_logloss: 0.368321
[10]	training's binary_logloss: 0.393762	valid_0's binary_logloss: 0.348326
[11]	training's binary_logloss: 0.382748	valid_0's binary_logloss: 0.330767
[12]	training's binary_logloss: 0.373187	valid_0's binary_logloss: 0.315088
[13]	training's binary_logloss: 0.364889	valid_0's binary_logloss: 0.301352
[14]	training's binary

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.631791	valid_0's binary_logloss: 0.573694
[2]	training's binary_logloss: 0.583687	valid_0's binary_logloss: 0.525915
[3]	training's binary_logloss: 0.54378	valid_0's binary_logloss: 0.486481
[4]	training's binary_logloss: 0.510306	valid_0's binary_logloss: 0.453519
[5]	training's binary_logloss: 0.482008	valid_0's binary_logloss: 0.425861
[6]	training's binary_logloss: 0.457948	valid_0's binary_logloss: 0.402628
[7]	training's binary_logloss: 0.437357	valid_0's binary_logloss: 0.382742
[8]	training's binary_logloss: 0.419676	valid_0's binary_logloss: 0.365839
[9]	training's binary_logloss: 0.404424	valid_0's binary_logloss: 0.351471
[10]	training's binary_logloss: 0.391245	valid_0's binary_logloss: 0.33915
[11]	training's binary_logloss: 0.379843	valid_0's binary_logloss: 0.328628
[12]	training's binary_logloss: 0.369938	valid_0's binary_logloss: 0.319497
[13]	training's binary_logloss: 0.361335	valid_0's binary_logloss: 0.311743
[14]	training's binary_

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[32]	training's binary_logloss: 0.312347	valid_0's binary_logloss: 0.184829
[33]	training's binary_logloss: 0.311734	valid_0's binary_logloss: 0.183167
[34]	training's binary_logloss: 0.311193	valid_0's binary_logloss: 0.18171
[35]	training's binary_logloss: 0.310713	valid_0's binary_logloss: 0.180433
[36]	training's binary_logloss: 0.310288	valid_0's binary_logloss: 0.179262
[37]	training's binary_logloss: 0.309917	valid_0's binary_logloss: 0.178293
[38]	training's binary_logloss: 0.309585	valid_0's binary_logloss: 0.177412
[39]	training's binary_logloss: 0.309288	valid_0's binary_logloss: 0.176528
[40]	training's binary_logloss: 0.309017	valid_0's binary_logloss: 0.175752
[41]	training's binary_logloss: 0.308789	valid_0's binary_logloss: 0.175111
[42]	training's binary_logloss: 0.308582	valid_0's binary_logloss: 0.174474
[43]	training's binary_logloss: 0.308401	valid_0's binary_logloss: 0.173844
[44]	training's binary_logloss: 0.308234	valid_0's binary_logloss: 0.17333
[45]	training'

In [18]:
# Range

import lightgbm

#Implementing cross validation 
#kf = KFold(n_splits=23, random_state=1, shuffle=True)
model = lightgbm.LGBMClassifier(learning_rate=0.1, n_estimators=100, max_depth=5, random_state=0)

from time import time
import timeit #imports timeit module
start_time = timeit.default_timer() #defines start time so computational time can be calculated

acc_score = [];
Truth = [];
Output = [];
n_estimators_list = []
max_depth_list = []

x_values = ['Range']
# 'StoS', 'StoR', 'StoL', 'RtoS', 'RtoR', 'RtoL', 'LtoS',
#        'LtoR', 'LtoL', 'STD', 'CoefVar', 'Range', 'Volatility', 'ShEn',
#        'AppEn', 'SampEn', 'IQR', 'Var', 'Rmean_Var', 'Mean_Absolute_Deviation'
y_values = ['Rhythm']
df = features_maindf

for idx, subject in enumerate(good_list):
    
    train_index = ~df['Subject'].str.contains(subject)
    test_index = df['Subject'].str.contains(subject)
    X_train , X_test = df.loc[train_index,x_values], df.loc[test_index,x_values]
    y_train , y_test = df.loc[train_index,y_values].values.ravel(), df.loc[test_index,y_values]

    # Create the LightGBM data containers
    model.fit(X_train,y_train,eval_set=[(X_test,y_test),(X_train,y_train)],
          eval_metric='logloss')

    pred_values = model.predict(X_test)
     
    acc = accuracy_score(y_test, pred_values)
    acc_score.append(acc)
    
    Truth.extend(y_test.values.reshape(y_test.shape[0])); ## it is a list
    Output.extend(pred_values); ## it is a list  
    
    #print(model.feature_importances_)
#     Importance = pd.DataFrame({'Importance':(model.feature_importances_*100)}, 
#                           index = (X_train.columns))
#     Importance.sort_values(by = 'Importance', 
#                        axis = 0, 
#                        ascending = True).plot(kind = 'barh', 
#                                               color = 'r')
#     plt.xlabel('Variable Importance')
#     plt.gca().legend_ = None
    #plt.savefig('plot1.png')


elapsed = timeit.default_timer() - start_time #gives total computation time
print("---Run time is %s seconds ---" % elapsed) #prints computation time
print()

print('Accuracy of each fold: \n {}'.format(acc_score))
print()
print('Avg accuracy : \n{}'.format(np.mean(acc_score))); 
print()
print('Std of accuracy : \n{}'.format(np.std(acc_score)))

print(confusion_matrix(Truth, Output))
print(classification_report(Truth, Output))
print(acc_score)
print(elapsed)

[1]	training's binary_logloss: 0.646192	valid_0's binary_logloss: 0.579506
[2]	training's binary_logloss: 0.609411	valid_0's binary_logloss: 0.537448
[3]	training's binary_logloss: 0.578896	valid_0's binary_logloss: 0.503208
[4]	training's binary_logloss: 0.553319	valid_0's binary_logloss: 0.474831
[5]	training's binary_logloss: 0.531738	valid_0's binary_logloss: 0.451203
[6]	training's binary_logloss: 0.513424	valid_0's binary_logloss: 0.431426
[7]	training's binary_logloss: 0.497792	valid_0's binary_logloss: 0.414609
[8]	training's binary_logloss: 0.484404	valid_0's binary_logloss: 0.400564
[9]	training's binary_logloss: 0.472886	valid_0's binary_logloss: 0.388426
[10]	training's binary_logloss: 0.462955	valid_0's binary_logloss: 0.37823
[11]	training's binary_logloss: 0.454323	valid_0's binary_logloss: 0.369484
[12]	training's binary_logloss: 0.446841	valid_0's binary_logloss: 0.361993
[13]	training's binary_logloss: 0.44035	valid_0's binary_logloss: 0.355407
[14]	training's binary_

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[69]	training's binary_logloss: 0.393281	valid_0's binary_logloss: 0.308476
[70]	training's binary_logloss: 0.393269	valid_0's binary_logloss: 0.308495
[71]	training's binary_logloss: 0.393245	valid_0's binary_logloss: 0.308565
[72]	training's binary_logloss: 0.393236	valid_0's binary_logloss: 0.30859
[73]	training's binary_logloss: 0.393211	valid_0's binary_logloss: 0.308581
[74]	training's binary_logloss: 0.393202	valid_0's binary_logloss: 0.308612
[75]	training's binary_logloss: 0.39319	valid_0's binary_logloss: 0.308636
[76]	training's binary_logloss: 0.393184	valid_0's binary_logloss: 0.308645
[77]	training's binary_logloss: 0.393176	valid_0's binary_logloss: 0.308616
[78]	training's binary_logloss: 0.39317	valid_0's binary_logloss: 0.308625
[79]	training's binary_logloss: 0.393147	valid_0's binary_logloss: 0.308546
[80]	training's binary_logloss: 0.393127	valid_0's binary_logloss: 0.308523
[81]	training's binary_logloss: 0.393118	valid_0's binary_logloss: 0.308533
[82]	training's

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[12]	training's binary_logloss: 0.453491	valid_0's binary_logloss: 0.291373
[13]	training's binary_logloss: 0.44715	valid_0's binary_logloss: 0.280493
[14]	training's binary_logloss: 0.4416	valid_0's binary_logloss: 0.270853
[15]	training's binary_logloss: 0.436799	valid_0's binary_logloss: 0.262308
[16]	training's binary_logloss: 0.432587	valid_0's binary_logloss: 0.254799
[17]	training's binary_logloss: 0.42889	valid_0's binary_logloss: 0.248128
[18]	training's binary_logloss: 0.425648	valid_0's binary_logloss: 0.242217
[19]	training's binary_logloss: 0.422809	valid_0's binary_logloss: 0.236916
[20]	training's binary_logloss: 0.420308	valid_0's binary_logloss: 0.232175
[21]	training's binary_logloss: 0.418063	valid_0's binary_logloss: 0.227996
[22]	training's binary_logloss: 0.416101	valid_0's binary_logloss: 0.224315
[23]	training's binary_logloss: 0.414386	valid_0's binary_logloss: 0.220968
[24]	training's binary_logloss: 0.412869	valid_0's binary_logloss: 0.218058
[25]	training's 

...

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.645924	valid_0's binary_logloss: 0.579681
[2]	training's binary_logloss: 0.609255	valid_0's binary_logloss: 0.537049
[3]	training's binary_logloss: 0.578802	valid_0's binary_logloss: 0.50198
[4]	training's binary_logloss: 0.55329	valid_0's binary_logloss: 0.472876
[5]	training's binary_logloss: 0.531758	valid_0's binary_logloss: 0.4481
[6]	training's binary_logloss: 0.513478	valid_0's binary_logloss: 0.427572
[7]	training's binary_logloss: 0.497879	valid_0's binary_logloss: 0.409763
[8]	training's binary_logloss: 0.484517	valid_0's binary_logloss: 0.394571
[9]	training's binary_logloss: 0.473019	valid_0's binary_logloss: 0.381836
[10]	training's binary_logloss: 0.463105	valid_0's binary_logloss: 0.370592
[11]	training's binary_logloss: 0.454522	valid_0's binary_logloss: 0.361276
[12]	training's binary_logloss: 0.447085	valid_0's binary_logloss: 0.352824
[13]	training's binary_logloss: 0.440602	valid_0's binary_logloss: 0.345508
[14]	training's binary_lo

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.640896	valid_0's binary_logloss: 0.708251
[2]	training's binary_logloss: 0.605212	valid_0's binary_logloss: 0.659372
[3]	training's binary_logloss: 0.575541	valid_0's binary_logloss: 0.617965
[4]	training's binary_logloss: 0.550639	valid_0's binary_logloss: 0.582414
[5]	training's binary_logloss: 0.529584	valid_0's binary_logloss: 0.551855
[6]	training's binary_logloss: 0.51172	valid_0's binary_logloss: 0.525261
[7]	training's binary_logloss: 0.496475	valid_0's binary_logloss: 0.502065
[8]	training's binary_logloss: 0.483379	valid_0's binary_logloss: 0.481936
[9]	training's binary_logloss: 0.472126	valid_0's binary_logloss: 0.464166
[10]	training's binary_logloss: 0.462425	valid_0's binary_logloss: 0.448632
[11]	training's binary_logloss: 0.454016	valid_0's binary_logloss: 0.434868
[12]	training's binary_logloss: 0.446694	valid_0's binary_logloss: 0.422739
[13]	training's binary_logloss: 0.440347	valid_0's binary_logloss: 0.411909
[14]	training's binary

              precision    recall  f1-score   support

           0       0.91      0.67      0.77     24743
           1       0.69      0.91      0.79     20225

    accuracy                           0.78     44968
   macro avg       0.80      0.79      0.78     44968
weighted avg       0.81      0.78      0.78     44968

[0.7768878718535469, 0.9127789046653144, 0.8494962216624685, 0.30755395683453235, 0.9143155694879833, 0.8754563894523326, 0.9159271368519384, 0.8495575221238938, 0.8383534136546185, 0.5352811466372657, 0.9727767695099818, 0.6999282124910265, 0.5537414965986395, 0.9713375796178344, 0.4275603663613655, 0.875498449268941, 0.7936943111720356, 0.9319099826889786, 0.3723584108199493, 0.8785046728971962, 0.9503849443969205, 0.815442561205273, 0.9424947145877378]
6.099570999999997


In [19]:
# Volatility

import lightgbm

#Implementing cross validation 
#kf = KFold(n_splits=23, random_state=1, shuffle=True)
model = lightgbm.LGBMClassifier(learning_rate=0.1, n_estimators=100, max_depth=5, random_state=0)

from time import time
import timeit #imports timeit module
start_time = timeit.default_timer() #defines start time so computational time can be calculated

acc_score = [];
Truth = [];
Output = [];
n_estimators_list = []
max_depth_list = []

x_values = ['Volatility']
# 'StoS', 'StoR', 'StoL', 'RtoS', 'RtoR', 'RtoL', 'LtoS',
#        'LtoR', 'LtoL', 'STD', 'CoefVar', 'Range', 'Volatility', 'ShEn',
#        'AppEn', 'SampEn', 'IQR', 'Var', 'Rmean_Var', 'Mean_Absolute_Deviation'
y_values = ['Rhythm']
df = features_maindf

for idx, subject in enumerate(good_list):
    
    train_index = ~df['Subject'].str.contains(subject)
    test_index = df['Subject'].str.contains(subject)
    X_train , X_test = df.loc[train_index,x_values], df.loc[test_index,x_values]
    y_train , y_test = df.loc[train_index,y_values].values.ravel(), df.loc[test_index,y_values]

    # Create the LightGBM data containers
    model.fit(X_train,y_train,eval_set=[(X_test,y_test),(X_train,y_train)],
          eval_metric='logloss')

    pred_values = model.predict(X_test)
     
    acc = accuracy_score(y_test, pred_values)
    acc_score.append(acc)
    
    Truth.extend(y_test.values.reshape(y_test.shape[0])); ## it is a list
    Output.extend(pred_values); ## it is a list  
    
    #print(model.feature_importances_)
#     Importance = pd.DataFrame({'Importance':(model.feature_importances_*100)}, 
#                           index = (X_train.columns))
#     Importance.sort_values(by = 'Importance', 
#                        axis = 0, 
#                        ascending = True).plot(kind = 'barh', 
#                                               color = 'r')
#     plt.xlabel('Variable Importance')
#     plt.gca().legend_ = None
    #plt.savefig('plot1.png')


elapsed = timeit.default_timer() - start_time #gives total computation time
print("---Run time is %s seconds ---" % elapsed) #prints computation time
print()

print('Accuracy of each fold: \n {}'.format(acc_score))
print()
print('Avg accuracy : \n{}'.format(np.mean(acc_score))); 
print()
print('Std of accuracy : \n{}'.format(np.std(acc_score)))

print(confusion_matrix(Truth, Output))
print(classification_report(Truth, Output))
print(acc_score)
print(elapsed)

[1]	training's binary_logloss: 0.64695	valid_0's binary_logloss: 0.579632
[2]	training's binary_logloss: 0.610785	valid_0's binary_logloss: 0.537784
[3]	training's binary_logloss: 0.580773	valid_0's binary_logloss: 0.503599
[4]	training's binary_logloss: 0.555633	valid_0's binary_logloss: 0.475414
[5]	training's binary_logloss: 0.534415	valid_0's binary_logloss: 0.451977
[6]	training's binary_logloss: 0.516406	valid_0's binary_logloss: 0.432335
[7]	training's binary_logloss: 0.501049	valid_0's binary_logloss: 0.415719
[8]	training's binary_logloss: 0.48788	valid_0's binary_logloss: 0.401624
[9]	training's binary_logloss: 0.476558	valid_0's binary_logloss: 0.389597
[10]	training's binary_logloss: 0.466791	valid_0's binary_logloss: 0.379428
[11]	training's binary_logloss: 0.458341	valid_0's binary_logloss: 0.370623
[12]	training's binary_logloss: 0.45101	valid_0's binary_logloss: 0.363097
[13]	training's binary_logloss: 0.444645	valid_0's binary_logloss: 0.356509
[14]	training's binary_l

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[65]	training's binary_logloss: 0.398789	valid_0's binary_logloss: 0.308778
[66]	training's binary_logloss: 0.398777	valid_0's binary_logloss: 0.308746
[67]	training's binary_logloss: 0.398764	valid_0's binary_logloss: 0.308669
[68]	training's binary_logloss: 0.398745	valid_0's binary_logloss: 0.308636
[69]	training's binary_logloss: 0.39873	valid_0's binary_logloss: 0.308619
[70]	training's binary_logloss: 0.398714	valid_0's binary_logloss: 0.308621
[71]	training's binary_logloss: 0.398695	valid_0's binary_logloss: 0.308623
[72]	training's binary_logloss: 0.398681	valid_0's binary_logloss: 0.308622
[73]	training's binary_logloss: 0.398672	valid_0's binary_logloss: 0.308658
[74]	training's binary_logloss: 0.39866	valid_0's binary_logloss: 0.308645
[75]	training's binary_logloss: 0.398616	valid_0's binary_logloss: 0.308665
[76]	training's binary_logloss: 0.398605	valid_0's binary_logloss: 0.308662
[77]	training's binary_logloss: 0.398596	valid_0's binary_logloss: 0.308662
[78]	training'

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[10]	training's binary_logloss: 0.472921	valid_0's binary_logloss: 0.320726
[11]	training's binary_logloss: 0.464711	valid_0's binary_logloss: 0.306834
[12]	training's binary_logloss: 0.457583	valid_0's binary_logloss: 0.29461
[13]	training's binary_logloss: 0.451382	valid_0's binary_logloss: 0.283857
[14]	training's binary_logloss: 0.445976	valid_0's binary_logloss: 0.274368
[15]	training's binary_logloss: 0.441258	valid_0's binary_logloss: 0.265964
[16]	training's binary_logloss: 0.437129	valid_0's binary_logloss: 0.258537
[17]	training's binary_logloss: 0.433504	valid_0's binary_logloss: 0.251894
[18]	training's binary_logloss: 0.430323	valid_0's binary_logloss: 0.246025
[19]	training's binary_logloss: 0.427527	valid_0's binary_logloss: 0.240776
[20]	training's binary_logloss: 0.425064	valid_0's binary_logloss: 0.236136
[21]	training's binary_logloss: 0.422895	valid_0's binary_logloss: 0.231979
[22]	training's binary_logloss: 0.420984	valid_0's binary_logloss: 0.228309
[23]	training

...

[1]	training's binary_logloss: 0.64148	valid_0's binary_logloss: 0.714972
[2]	training's binary_logloss: 0.606508	valid_0's binary_logloss: 0.665142
[3]	training's binary_logloss: 0.5774	valid_0's binary_logloss: 0.622827
[4]	training's binary_logloss: 0.552981	valid_0's binary_logloss: 0.586571
[5]	training's binary_logloss: 0.532356	valid_0's binary_logloss: 0.555314
[6]	training's binary_logloss: 0.514834	valid_0's binary_logloss: 0.528206
[7]	training's binary_logloss: 0.499871	valid_0's binary_logloss: 0.504553
[8]	training's binary_logloss: 0.487048	valid_0's binary_logloss: 0.483891
[9]	training's binary_logloss: 0.476017	valid_0's binary_logloss: 0.465735
[10]	training's binary_logloss: 0.466495	valid_0's binary_logloss: 0.449737
[11]	training's binary_logloss: 0.458245	valid_0's binary_logloss: 0.435673
[12]	training's binary_logloss: 0.451089	valid_0's binary_logloss: 0.423178
[13]	training's binary_logloss: 0.444866	valid_0's binary_logloss: 0.412138
[14]	training's binary_l

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[19]	training's binary_logloss: 0.420536	valid_0's binary_logloss: 0.318189
[20]	training's binary_logloss: 0.418014	valid_0's binary_logloss: 0.315343
[21]	training's binary_logloss: 0.415789	valid_0's binary_logloss: 0.312715
[22]	training's binary_logloss: 0.413838	valid_0's binary_logloss: 0.310501
[23]	training's binary_logloss: 0.412114	valid_0's binary_logloss: 0.30859
[24]	training's binary_logloss: 0.410589	valid_0's binary_logloss: 0.306946
[25]	training's binary_logloss: 0.409246	valid_0's binary_logloss: 0.305518
[26]	training's binary_logloss: 0.408055	valid_0's binary_logloss: 0.30417
[27]	training's binary_logloss: 0.407003	valid_0's binary_logloss: 0.302962
[28]	training's binary_logloss: 0.406079	valid_0's binary_logloss: 0.301932
[29]	training's binary_logloss: 0.405249	valid_0's binary_logloss: 0.300962
[30]	training's binary_logloss: 0.404513	valid_0's binary_logloss: 0.300039
[31]	training's binary_logloss: 0.403877	valid_0's binary_logloss: 0.299294
[32]	training'

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[2]	training's binary_logloss: 0.606602	valid_0's binary_logloss: 0.660159
[3]	training's binary_logloss: 0.577438	valid_0's binary_logloss: 0.618925
[4]	training's binary_logloss: 0.552954	valid_0's binary_logloss: 0.583555
[5]	training's binary_logloss: 0.532274	valid_0's binary_logloss: 0.553079
[6]	training's binary_logloss: 0.514701	valid_0's binary_logloss: 0.526692
[7]	training's binary_logloss: 0.499706	valid_0's binary_logloss: 0.503688
[8]	training's binary_logloss: 0.486852	valid_0's binary_logloss: 0.48362
[9]	training's binary_logloss: 0.475798	valid_0's binary_logloss: 0.465994
[10]	training's binary_logloss: 0.466251	valid_0's binary_logloss: 0.450466
[11]	training's binary_logloss: 0.45798	valid_0's binary_logloss: 0.436748
[12]	training's binary_logloss: 0.450811	valid_0's binary_logloss: 0.424627
[13]	training's binary_logloss: 0.444574	valid_0's binary_logloss: 0.413901
[14]	training's binary_logloss: 0.439135	valid_0's binary_logloss: 0.404408
[15]	training's binary

In [20]:
# Shannon Entropy

import lightgbm

#Implementing cross validation 
#kf = KFold(n_splits=23, random_state=1, shuffle=True)
model = lightgbm.LGBMClassifier(learning_rate=0.1, n_estimators=100, max_depth=5, random_state=0)

from time import time
import timeit #imports timeit module
start_time = timeit.default_timer() #defines start time so computational time can be calculated

acc_score = [];
Truth = [];
Output = [];
n_estimators_list = []
max_depth_list = []

x_values = ['ShEn']
# 'StoS', 'StoR', 'StoL', 'RtoS', 'RtoR', 'RtoL', 'LtoS',
#        'LtoR', 'LtoL', 'STD', 'CoefVar', 'Range', 'Volatility', 'ShEn',
#        'AppEn', 'SampEn', 'IQR', 'Var', 'Rmean_Var', 'Mean_Absolute_Deviation'
y_values = ['Rhythm']
df = features_maindf

for idx, subject in enumerate(good_list):
    
    train_index = ~df['Subject'].str.contains(subject)
    test_index = df['Subject'].str.contains(subject)
    X_train , X_test = df.loc[train_index,x_values], df.loc[test_index,x_values]
    y_train , y_test = df.loc[train_index,y_values].values.ravel(), df.loc[test_index,y_values]

    # Create the LightGBM data containers
    model.fit(X_train,y_train,eval_set=[(X_test,y_test),(X_train,y_train)],
          eval_metric='logloss')

    pred_values = model.predict(X_test)
     
    acc = accuracy_score(y_test, pred_values)
    acc_score.append(acc)
    
    Truth.extend(y_test.values.reshape(y_test.shape[0])); ## it is a list
    Output.extend(pred_values); ## it is a list  
    
    #print(model.feature_importances_)
#     Importance = pd.DataFrame({'Importance':(model.feature_importances_*100)}, 
#                           index = (X_train.columns))
#     Importance.sort_values(by = 'Importance', 
#                        axis = 0, 
#                        ascending = True).plot(kind = 'barh', 
#                                               color = 'r')
#     plt.xlabel('Variable Importance')
#     plt.gca().legend_ = None
    #plt.savefig('plot1.png')


elapsed = timeit.default_timer() - start_time #gives total computation time
print("---Run time is %s seconds ---" % elapsed) #prints computation time
print()

print('Accuracy of each fold: \n {}'.format(acc_score))
print()
print('Avg accuracy : \n{}'.format(np.mean(acc_score))); 
print()
print('Std of accuracy : \n{}'.format(np.std(acc_score)))

print(confusion_matrix(Truth, Output))
print(classification_report(Truth, Output))
print(acc_score)
print(elapsed)

[1]	training's binary_logloss: 0.628409	valid_0's binary_logloss: 0.566019
[2]	training's binary_logloss: 0.577207	valid_0's binary_logloss: 0.512628
[3]	training's binary_logloss: 0.534722	valid_0's binary_logloss: 0.468675
[4]	training's binary_logloss: 0.499124	valid_0's binary_logloss: 0.4321
[5]	training's binary_logloss: 0.469038	valid_0's binary_logloss: 0.40135
[6]	training's binary_logloss: 0.443461	valid_0's binary_logloss: 0.375389
[7]	training's binary_logloss: 0.421608	valid_0's binary_logloss: 0.353386
[8]	training's binary_logloss: 0.40287	valid_0's binary_logloss: 0.334719
[9]	training's binary_logloss: 0.38668	valid_0's binary_logloss: 0.318667
[10]	training's binary_logloss: 0.372694	valid_0's binary_logloss: 0.304934
[11]	training's binary_logloss: 0.3606	valid_0's binary_logloss: 0.29321
[12]	training's binary_logloss: 0.350124	valid_0's binary_logloss: 0.283153
[13]	training's binary_logloss: 0.34093	valid_0's binary_logloss: 0.274655
[14]	training's binary_logloss

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[27]	training's binary_logloss: 0.2878	valid_0's binary_logloss: 0.228865
[28]	training's binary_logloss: 0.286559	valid_0's binary_logloss: 0.228052
[29]	training's binary_logloss: 0.28547	valid_0's binary_logloss: 0.227177
[30]	training's binary_logloss: 0.284549	valid_0's binary_logloss: 0.226551
[31]	training's binary_logloss: 0.283701	valid_0's binary_logloss: 0.225913
[32]	training's binary_logloss: 0.282902	valid_0's binary_logloss: 0.225355
[33]	training's binary_logloss: 0.282225	valid_0's binary_logloss: 0.225051
[34]	training's binary_logloss: 0.281668	valid_0's binary_logloss: 0.224679
[35]	training's binary_logloss: 0.281117	valid_0's binary_logloss: 0.224362
[36]	training's binary_logloss: 0.280591	valid_0's binary_logloss: 0.224011
[37]	training's binary_logloss: 0.280096	valid_0's binary_logloss: 0.223701
[38]	training's binary_logloss: 0.279745	valid_0's binary_logloss: 0.223378
[39]	training's binary_logloss: 0.279404	valid_0's binary_logloss: 0.223194
[40]	training's

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[15]	training's binary_logloss: 0.327541	valid_0's binary_logloss: 0.309397
[16]	training's binary_logloss: 0.321459	valid_0's binary_logloss: 0.3028
[17]	training's binary_logloss: 0.316165	valid_0's binary_logloss: 0.296967
[18]	training's binary_logloss: 0.311616	valid_0's binary_logloss: 0.291807
[19]	training's binary_logloss: 0.307602	valid_0's binary_logloss: 0.287234
[20]	training's binary_logloss: 0.304099	valid_0's binary_logloss: 0.283199
[21]	training's binary_logloss: 0.300991	valid_0's binary_logloss: 0.279527
[22]	training's binary_logloss: 0.298246	valid_0's binary_logloss: 0.276368
[23]	training's binary_logloss: 0.295848	valid_0's binary_logloss: 0.273402
[24]	training's binary_logloss: 0.293789	valid_0's binary_logloss: 0.27089
[25]	training's binary_logloss: 0.291939	valid_0's binary_logloss: 0.268547
[26]	training's binary_logloss: 0.29035	valid_0's binary_logloss: 0.266486
[27]	training's binary_logloss: 0.28892	valid_0's binary_logloss: 0.26466
[28]	training's bi

...

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.628142	valid_0's binary_logloss: 0.564896
[2]	training's binary_logloss: 0.577103	valid_0's binary_logloss: 0.50972
[3]	training's binary_logloss: 0.534787	valid_0's binary_logloss: 0.463904
[4]	training's binary_logloss: 0.499333	valid_0's binary_logloss: 0.42547
[5]	training's binary_logloss: 0.469388	valid_0's binary_logloss: 0.392961
[6]	training's binary_logloss: 0.443933	valid_0's binary_logloss: 0.365433
[7]	training's binary_logloss: 0.422185	valid_0's binary_logloss: 0.34181
[8]	training's binary_logloss: 0.403475	valid_0's binary_logloss: 0.321328
[9]	training's binary_logloss: 0.387395	valid_0's binary_logloss: 0.303693
[10]	training's binary_logloss: 0.373506	valid_0's binary_logloss: 0.288489
[11]	training's binary_logloss: 0.361487	valid_0's binary_logloss: 0.275317
[12]	training's binary_logloss: 0.351077	valid_0's binary_logloss: 0.263915
[13]	training's binary_logloss: 0.341947	valid_0's binary_logloss: 0.25404
[14]	training's binary_lo

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.623376	valid_0's binary_logloss: 0.677151
[2]	training's binary_logloss: 0.573661	valid_0's binary_logloss: 0.604134
[3]	training's binary_logloss: 0.532491	valid_0's binary_logloss: 0.542942
[4]	training's binary_logloss: 0.498033	valid_0's binary_logloss: 0.491272
[5]	training's binary_logloss: 0.468949	valid_0's binary_logloss: 0.447191
[6]	training's binary_logloss: 0.44425	valid_0's binary_logloss: 0.409274
[7]	training's binary_logloss: 0.423166	valid_0's binary_logloss: 0.376397
[8]	training's binary_logloss: 0.405096	valid_0's binary_logloss: 0.347729
[9]	training's binary_logloss: 0.389535	valid_0's binary_logloss: 0.322703
[10]	training's binary_logloss: 0.376094	valid_0's binary_logloss: 0.300389
[11]	training's binary_logloss: 0.364462	valid_0's binary_logloss: 0.280736
[12]	training's binary_logloss: 0.354395	valid_0's binary_logloss: 0.263345
[13]	training's binary_logloss: 0.345671	valid_0's binary_logloss: 0.247943
[14]	training's binary

              precision    recall  f1-score   support

           0       0.91      0.84      0.88     24743
           1       0.82      0.90      0.86     20225

    accuracy                           0.87     44968
   macro avg       0.87      0.87      0.87     44968
weighted avg       0.87      0.87      0.87     44968

[0.8975972540045767, 0.9257606490872211, 0.9911838790931989, 0.8165467625899281, 0.9827586206896551, 0.8855983772819472, 0.8612797758056983, 0.9816201497617427, 0.8975903614457831, 0.737045203969129, 0.9764065335753176, 0.9547738693467337, 0.7850340136054422, 0.9490445859872612, 0.5295587010824313, 0.976517501107665, 0.9465387251542152, 0.860934795152914, 0.4661876584953508, 0.8867509620670698, 0.9854576561163387, 0.9146264908976773, 0.9894291754756871]
6.782236299999994


In [21]:
# Approximate Entropy

import lightgbm

#Implementing cross validation 
#kf = KFold(n_splits=23, random_state=1, shuffle=True)
model = lightgbm.LGBMClassifier(learning_rate=0.1, n_estimators=100, max_depth=5, random_state=0)

from time import time
import timeit #imports timeit module
start_time = timeit.default_timer() #defines start time so computational time can be calculated

acc_score = [];
Truth = [];
Output = [];
n_estimators_list = []
max_depth_list = []

x_values = ['AppEn']
# 'StoS', 'StoR', 'StoL', 'RtoS', 'RtoR', 'RtoL', 'LtoS',
#        'LtoR', 'LtoL', 'STD', 'CoefVar', 'Range', 'Volatility', 'ShEn',
#        'AppEn', 'SampEn', 'IQR', 'Var', 'Rmean_Var', 'Mean_Absolute_Deviation'
y_values = ['Rhythm']
df = features_maindf

for idx, subject in enumerate(good_list):
    
    train_index = ~df['Subject'].str.contains(subject)
    test_index = df['Subject'].str.contains(subject)
    X_train , X_test = df.loc[train_index,x_values], df.loc[test_index,x_values]
    y_train , y_test = df.loc[train_index,y_values].values.ravel(), df.loc[test_index,y_values]

    # Create the LightGBM data containers
    model.fit(X_train,y_train,eval_set=[(X_test,y_test),(X_train,y_train)],
          eval_metric='logloss')

    pred_values = model.predict(X_test)
     
    acc = accuracy_score(y_test, pred_values)
    acc_score.append(acc)
    
    Truth.extend(y_test.values.reshape(y_test.shape[0])); ## it is a list
    Output.extend(pred_values); ## it is a list  
    
    #print(model.feature_importances_)
#     Importance = pd.DataFrame({'Importance':(model.feature_importances_*100)}, 
#                           index = (X_train.columns))
#     Importance.sort_values(by = 'Importance', 
#                        axis = 0, 
#                        ascending = True).plot(kind = 'barh', 
#                                               color = 'r')
#     plt.xlabel('Variable Importance')
#     plt.gca().legend_ = None
    #plt.savefig('plot1.png')


elapsed = timeit.default_timer() - start_time #gives total computation time
print("---Run time is %s seconds ---" % elapsed) #prints computation time
print()

print('Accuracy of each fold: \n {}'.format(acc_score))
print()
print('Avg accuracy : \n{}'.format(np.mean(acc_score))); 
print()
print('Std of accuracy : \n{}'.format(np.std(acc_score)))

print(confusion_matrix(Truth, Output))
print(classification_report(Truth, Output))
print(acc_score)
print(elapsed)

[1]	training's binary_logloss: 0.622706	valid_0's binary_logloss: 0.570194
[2]	training's binary_logloss: 0.566824	valid_0's binary_logloss: 0.520222
[3]	training's binary_logloss: 0.520392	valid_0's binary_logloss: 0.479057
[4]	training's binary_logloss: 0.481321	valid_0's binary_logloss: 0.444876
[5]	training's binary_logloss: 0.448137	valid_0's binary_logloss: 0.416328
[6]	training's binary_logloss: 0.419735	valid_0's binary_logloss: 0.392324
[7]	training's binary_logloss: 0.395276	valid_0's binary_logloss: 0.37213
[8]	training's binary_logloss: 0.374117	valid_0's binary_logloss: 0.355151
[9]	training's binary_logloss: 0.355741	valid_0's binary_logloss: 0.34081
[10]	training's binary_logloss: 0.339711	valid_0's binary_logloss: 0.328745
[11]	training's binary_logloss: 0.325699	valid_0's binary_logloss: 0.318669
[12]	training's binary_logloss: 0.313423	valid_0's binary_logloss: 0.310249
[13]	training's binary_logloss: 0.302648	valid_0's binary_logloss: 0.303248
[14]	training's binary_

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[59]	training's binary_logloss: 0.223731	valid_0's binary_logloss: 0.304866
[60]	training's binary_logloss: 0.22369	valid_0's binary_logloss: 0.305095
[61]	training's binary_logloss: 0.223655	valid_0's binary_logloss: 0.305385
[62]	training's binary_logloss: 0.223633	valid_0's binary_logloss: 0.305506
[63]	training's binary_logloss: 0.223604	valid_0's binary_logloss: 0.30576
[64]	training's binary_logloss: 0.223588	valid_0's binary_logloss: 0.306072
[65]	training's binary_logloss: 0.22357	valid_0's binary_logloss: 0.306217
[66]	training's binary_logloss: 0.223499	valid_0's binary_logloss: 0.306151
[67]	training's binary_logloss: 0.223477	valid_0's binary_logloss: 0.306321
[68]	training's binary_logloss: 0.223465	valid_0's binary_logloss: 0.306531
[69]	training's binary_logloss: 0.223411	valid_0's binary_logloss: 0.30653
[70]	training's binary_logloss: 0.223402	valid_0's binary_logloss: 0.306746
[71]	training's binary_logloss: 0.22336	valid_0's binary_logloss: 0.306807
[72]	training's b

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[2]	training's binary_logloss: 0.567504	valid_0's binary_logloss: 0.529042
[3]	training's binary_logloss: 0.521615	valid_0's binary_logloss: 0.48106
[4]	training's binary_logloss: 0.483031	valid_0's binary_logloss: 0.440324
[5]	training's binary_logloss: 0.450253	valid_0's binary_logloss: 0.405577
[6]	training's binary_logloss: 0.422229	valid_0's binary_logloss: 0.375639
[7]	training's binary_logloss: 0.398117	valid_0's binary_logloss: 0.349681
[8]	training's binary_logloss: 0.377259	valid_0's binary_logloss: 0.32715
[9]	training's binary_logloss: 0.35915	valid_0's binary_logloss: 0.307489
[10]	training's binary_logloss: 0.343376	valid_0's binary_logloss: 0.290276
[11]	training's binary_logloss: 0.329594	valid_0's binary_logloss: 0.275077
[12]	training's binary_logloss: 0.317531	valid_0's binary_logloss: 0.261729
[13]	training's binary_logloss: 0.307014	valid_0's binary_logloss: 0.249996
[14]	training's binary_logloss: 0.297782	valid_0's binary_logloss: 0.239654
[15]	training's binary_

...

[1]	training's binary_logloss: 0.617228	valid_0's binary_logloss: 0.677356
[2]	training's binary_logloss: 0.562856	valid_0's binary_logloss: 0.599077
[3]	training's binary_logloss: 0.517774	valid_0's binary_logloss: 0.534502
[4]	training's binary_logloss: 0.479909	valid_0's binary_logloss: 0.480404
[5]	training's binary_logloss: 0.447797	valid_0's binary_logloss: 0.434407
[6]	training's binary_logloss: 0.420355	valid_0's binary_logloss: 0.395043
[7]	training's binary_logloss: 0.396764	valid_0's binary_logloss: 0.36104
[8]	training's binary_logloss: 0.376381	valid_0's binary_logloss: 0.331519
[9]	training's binary_logloss: 0.358686	valid_0's binary_logloss: 0.305695
[10]	training's binary_logloss: 0.34329	valid_0's binary_logloss: 0.283068
[11]	training's binary_logloss: 0.329859	valid_0's binary_logloss: 0.263165
[12]	training's binary_logloss: 0.318107	valid_0's binary_logloss: 0.245634
[13]	training's binary_logloss: 0.307845	valid_0's binary_logloss: 0.230121
[14]	training's binary_

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.622859	valid_0's binary_logloss: 0.564038
[2]	training's binary_logloss: 0.567517	valid_0's binary_logloss: 0.507631
[3]	training's binary_logloss: 0.521535	valid_0's binary_logloss: 0.460348
[4]	training's binary_logloss: 0.482864	valid_0's binary_logloss: 0.420274
[5]	training's binary_logloss: 0.450026	valid_0's binary_logloss: 0.386011
[6]	training's binary_logloss: 0.421919	valid_0's binary_logloss: 0.356427
[7]	training's binary_logloss: 0.397756	valid_0's binary_logloss: 0.330925
[8]	training's binary_logloss: 0.376863	valid_0's binary_logloss: 0.308739
[9]	training's binary_logloss: 0.358725	valid_0's binary_logloss: 0.289361
[10]	training's binary_logloss: 0.342908	valid_0's binary_logloss: 0.272302
[11]	training's binary_logloss: 0.329097	valid_0's binary_logloss: 0.257294
[12]	training's binary_logloss: 0.317012	valid_0's binary_logloss: 0.244104
[13]	training's binary_logloss: 0.306432	valid_0's binary_logloss: 0.232482
[14]	training's binar

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.617192	valid_0's binary_logloss: 0.678023
[2]	training's binary_logloss: 0.562529	valid_0's binary_logloss: 0.606105
[3]	training's binary_logloss: 0.517191	valid_0's binary_logloss: 0.546601
[4]	training's binary_logloss: 0.479118	valid_0's binary_logloss: 0.496571
[5]	training's binary_logloss: 0.446844	valid_0's binary_logloss: 0.454011
[6]	training's binary_logloss: 0.419248	valid_0's binary_logloss: 0.41753
[7]	training's binary_logloss: 0.395517	valid_0's binary_logloss: 0.385941
[8]	training's binary_logloss: 0.374999	valid_0's binary_logloss: 0.35852
[9]	training's binary_logloss: 0.357205	valid_0's binary_logloss: 0.334482
[10]	training's binary_logloss: 0.341712	valid_0's binary_logloss: 0.31338
[11]	training's binary_logloss: 0.328191	valid_0's binary_logloss: 0.294827
[12]	training's binary_logloss: 0.316369	valid_0's binary_logloss: 0.27843
[13]	training's binary_logloss: 0.306052	valid_0's binary_logloss: 0.263893
[14]	training's binary_lo

In [22]:
# Sample Entropy

import lightgbm

#Implementing cross validation 
#kf = KFold(n_splits=23, random_state=1, shuffle=True)
model = lightgbm.LGBMClassifier(learning_rate=0.1, n_estimators=100, max_depth=5, random_state=0)

from time import time
import timeit #imports timeit module
start_time = timeit.default_timer() #defines start time so computational time can be calculated

acc_score = [];
Truth = [];
Output = [];
n_estimators_list = []
max_depth_list = []

x_values = ['SampEn']
# 'StoS', 'StoR', 'StoL', 'RtoS', 'RtoR', 'RtoL', 'LtoS',
#        'LtoR', 'LtoL', 'STD', 'CoefVar', 'Range', 'Volatility', 'ShEn',
#        'AppEn', 'SampEn', 'IQR', 'Var', 'Rmean_Var', 'Mean_Absolute_Deviation'
y_values = ['Rhythm']
df = features_maindf

for idx, subject in enumerate(good_list):
    
    train_index = ~df['Subject'].str.contains(subject)
    test_index = df['Subject'].str.contains(subject)
    X_train , X_test = df.loc[train_index,x_values], df.loc[test_index,x_values]
    y_train , y_test = df.loc[train_index,y_values].values.ravel(), df.loc[test_index,y_values]

    # Create the LightGBM data containers
    model.fit(X_train,y_train,eval_set=[(X_test,y_test),(X_train,y_train)],
          eval_metric='logloss')

    pred_values = model.predict(X_test)
     
    acc = accuracy_score(y_test, pred_values)
    acc_score.append(acc)
    
    Truth.extend(y_test.values.reshape(y_test.shape[0])); ## it is a list
    Output.extend(pred_values); ## it is a list  
    
    #print(model.feature_importances_)
#     Importance = pd.DataFrame({'Importance':(model.feature_importances_*100)}, 
#                           index = (X_train.columns))
#     Importance.sort_values(by = 'Importance', 
#                        axis = 0, 
#                        ascending = True).plot(kind = 'barh', 
#                                               color = 'r')
#     plt.xlabel('Variable Importance')
#     plt.gca().legend_ = None
    #plt.savefig('plot1.png')


elapsed = timeit.default_timer() - start_time #gives total computation time
print("---Run time is %s seconds ---" % elapsed) #prints computation time
print()

print('Accuracy of each fold: \n {}'.format(acc_score))
print()
print('Avg accuracy : \n{}'.format(np.mean(acc_score))); 
print()
print('Std of accuracy : \n{}'.format(np.std(acc_score)))

print(confusion_matrix(Truth, Output))
print(classification_report(Truth, Output))
print(acc_score)
print(elapsed)

[1]	training's binary_logloss: 0.62283	valid_0's binary_logloss: 0.569078


C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[2]	training's binary_logloss: 0.567067	valid_0's binary_logloss: 0.518148
[3]	training's binary_logloss: 0.520824	valid_0's binary_logloss: 0.4761
[4]	training's binary_logloss: 0.481918	valid_0's binary_logloss: 0.441035
[5]	training's binary_logloss: 0.448787	valid_0's binary_logloss: 0.411854
[6]	training's binary_logloss: 0.420479	valid_0's binary_logloss: 0.387321
[7]	training's binary_logloss: 0.39612	valid_0's binary_logloss: 0.366612
[8]	training's binary_logloss: 0.375055	valid_0's binary_logloss: 0.34913
[9]	training's binary_logloss: 0.356761	valid_0's binary_logloss: 0.334331
[10]	training's binary_logloss: 0.340781	valid_0's binary_logloss: 0.321891
[11]	training's binary_logloss: 0.326807	valid_0's binary_logloss: 0.311435
[12]	training's binary_logloss: 0.314584	valid_0's binary_logloss: 0.302699
[13]	training's binary_logloss: 0.303876	valid_0's binary_logloss: 0.29538
[14]	training's binary_logloss: 0.294474	valid_0's binary_logloss: 0.289352
[15]	training's binary_lo

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.62279	valid_0's binary_logloss: 0.586814
[2]	training's binary_logloss: 0.567608	valid_0's binary_logloss: 0.529791
[3]	training's binary_logloss: 0.521759	valid_0's binary_logloss: 0.481913
[4]	training's binary_logloss: 0.483198	valid_0's binary_logloss: 0.441298
[5]	training's binary_logloss: 0.450532	valid_0's binary_logloss: 0.406593
[6]	training's binary_logloss: 0.42256	valid_0's binary_logloss: 0.376744
[7]	training's binary_logloss: 0.398533	valid_0's binary_logloss: 0.350861
[8]	training's binary_logloss: 0.377737	valid_0's binary_logloss: 0.328384
[9]	training's binary_logloss: 0.359705	valid_0's binary_logloss: 0.308767
[10]	training's binary_logloss: 0.343962	valid_0's binary_logloss: 0.291492
[11]	training's binary_logloss: 0.330243	valid_0's binary_logloss: 0.276306
[12]	training's binary_logloss: 0.318246	valid_0's binary_logloss: 0.26295
[13]	training's binary_logloss: 0.307712	valid_0's binary_logloss: 0.251187
[14]	training's binary_l

...

[1]	training's binary_logloss: 0.61732	valid_0's binary_logloss: 0.678086
[2]	training's binary_logloss: 0.563001	valid_0's binary_logloss: 0.600364
[3]	training's binary_logloss: 0.517985	valid_0's binary_logloss: 0.536192
[4]	training's binary_logloss: 0.480214	valid_0's binary_logloss: 0.482337
[5]	training's binary_logloss: 0.448188	valid_0's binary_logloss: 0.436617
[6]	training's binary_logloss: 0.42083	valid_0's binary_logloss: 0.397429
[7]	training's binary_logloss: 0.39733	valid_0's binary_logloss: 0.363588
[8]	training's binary_logloss: 0.377023	valid_0's binary_logloss: 0.334186
[9]	training's binary_logloss: 0.359422	valid_0's binary_logloss: 0.308509
[10]	training's binary_logloss: 0.344092	valid_0's binary_logloss: 0.285979
[11]	training's binary_logloss: 0.330706	valid_0's binary_logloss: 0.266128
[12]	training's binary_logloss: 0.319019	valid_0's binary_logloss: 0.248623
[13]	training's binary_logloss: 0.308763	valid_0's binary_logloss: 0.233135
[14]	training's binary_l

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[13]	training's binary_logloss: 0.306874	valid_0's binary_logloss: 0.241517
[14]	training's binary_logloss: 0.297627	valid_0's binary_logloss: 0.23177
[15]	training's binary_logloss: 0.289523	valid_0's binary_logloss: 0.223254
[16]	training's binary_logloss: 0.282392	valid_0's binary_logloss: 0.215703
[17]	training's binary_logloss: 0.276122	valid_0's binary_logloss: 0.209006
[18]	training's binary_logloss: 0.270579	valid_0's binary_logloss: 0.203159
[19]	training's binary_logloss: 0.265703	valid_0's binary_logloss: 0.197945
[20]	training's binary_logloss: 0.26139	valid_0's binary_logloss: 0.193385
[21]	training's binary_logloss: 0.257597	valid_0's binary_logloss: 0.18929
[22]	training's binary_logloss: 0.254254	valid_0's binary_logloss: 0.185715
[23]	training's binary_logloss: 0.251307	valid_0's binary_logloss: 0.182537
[24]	training's binary_logloss: 0.248725	valid_0's binary_logloss: 0.179817
[25]	training's binary_logloss: 0.246451	valid_0's binary_logloss: 0.177396
[26]	training's

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.617279	valid_0's binary_logloss: 0.679347
[2]	training's binary_logloss: 0.562688	valid_0's binary_logloss: 0.608381
[3]	training's binary_logloss: 0.517421	valid_0's binary_logloss: 0.549444
[4]	training's binary_logloss: 0.479414	valid_0's binary_logloss: 0.499834
[5]	training's binary_logloss: 0.447195	valid_0's binary_logloss: 0.457648
[6]	training's binary_logloss: 0.419718	valid_0's binary_logloss: 0.421439
[7]	training's binary_logloss: 0.3961	valid_0's binary_logloss: 0.390149
[8]	training's binary_logloss: 0.375683	valid_0's binary_logloss: 0.362856
[9]	training's binary_logloss: 0.357943	valid_0's binary_logloss: 0.338922
[10]	training's binary_logloss: 0.342523	valid_0's binary_logloss: 0.317966
[11]	training's binary_logloss: 0.329056	valid_0's binary_logloss: 0.299451
[12]	training's binary_logloss: 0.317277	valid_0's binary_logloss: 0.28305
[13]	training's binary_logloss: 0.306973	valid_0's binary_logloss: 0.268571
[14]	training's binary_l

In [23]:
# Interquartile Range

import lightgbm

#Implementing cross validation 
#kf = KFold(n_splits=23, random_state=1, shuffle=True)
model = lightgbm.LGBMClassifier(learning_rate=0.1, n_estimators=100, max_depth=5, random_state=0)

from time import time
import timeit #imports timeit module
start_time = timeit.default_timer() #defines start time so computational time can be calculated

acc_score = [];
Truth = [];
Output = [];
n_estimators_list = []
max_depth_list = []

x_values = ['IQR']
# 'StoS', 'StoR', 'StoL', 'RtoS', 'RtoR', 'RtoL', 'LtoS',
#        'LtoR', 'LtoL', 'STD', 'CoefVar', 'Range', 'Volatility', 'ShEn',
#        'AppEn', 'SampEn', 'IQR', 'Var', 'Rmean_Var', 'Mean_Absolute_Deviation'
y_values = ['Rhythm']
df = features_maindf

for idx, subject in enumerate(good_list):
    
    train_index = ~df['Subject'].str.contains(subject)
    test_index = df['Subject'].str.contains(subject)
    X_train , X_test = df.loc[train_index,x_values], df.loc[test_index,x_values]
    y_train , y_test = df.loc[train_index,y_values].values.ravel(), df.loc[test_index,y_values]

    # Create the LightGBM data containers
    model.fit(X_train,y_train,eval_set=[(X_test,y_test),(X_train,y_train)],
          eval_metric='logloss')

    pred_values = model.predict(X_test)
     
    acc = accuracy_score(y_test, pred_values)
    acc_score.append(acc)
    
    Truth.extend(y_test.values.reshape(y_test.shape[0])); ## it is a list
    Output.extend(pred_values); ## it is a list  
    
    #print(model.feature_importances_)
#     Importance = pd.DataFrame({'Importance':(model.feature_importances_*100)}, 
#                           index = (X_train.columns))
#     Importance.sort_values(by = 'Importance', 
#                        axis = 0, 
#                        ascending = True).plot(kind = 'barh', 
#                                               color = 'r')
#     plt.xlabel('Variable Importance')
#     plt.gca().legend_ = None
    #plt.savefig('plot1.png')


elapsed = timeit.default_timer() - start_time #gives total computation time
print("---Run time is %s seconds ---" % elapsed) #prints computation time
print()

print('Accuracy of each fold: \n {}'.format(acc_score))
print()
print('Avg accuracy : \n{}'.format(np.mean(acc_score))); 
print()
print('Std of accuracy : \n{}'.format(np.std(acc_score)))

print(confusion_matrix(Truth, Output))
print(classification_report(Truth, Output))
print(acc_score)
print(elapsed)

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.620035	valid_0's binary_logloss: 0.566746
[2]	training's binary_logloss: 0.561998	valid_0's binary_logloss: 0.513759
[3]	training's binary_logloss: 0.513831	valid_0's binary_logloss: 0.469944
[4]	training's binary_logloss: 0.473414	valid_0's binary_logloss: 0.433469
[5]	training's binary_logloss: 0.439194	valid_0's binary_logloss: 0.402763
[6]	training's binary_logloss: 0.410037	valid_0's binary_logloss: 0.376889
[7]	training's binary_logloss: 0.385021	valid_0's binary_logloss: 0.354926
[8]	training's binary_logloss: 0.363504	valid_0's binary_logloss: 0.336218
[9]	training's binary_logloss: 0.344938	valid_0's binary_logloss: 0.320357
[10]	training's binary_logloss: 0.328861	valid_0's binary_logloss: 0.306749
[11]	training's binary_logloss: 0.314898	valid_0's binary_logloss: 0.295019
[12]	training's binary_logloss: 0.302757	valid_0's binary_logloss: 0.284971
[13]	training's binary_logloss: 0.29219	valid_0's binary_logloss: 0.276352
[14]	training's binary

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.619652	valid_0's binary_logloss: 0.58656
[2]	training's binary_logloss: 0.561898	valid_0's binary_logloss: 0.529847
[3]	training's binary_logloss: 0.513977	valid_0's binary_logloss: 0.482448
[4]	training's binary_logloss: 0.47376	valid_0's binary_logloss: 0.442595
[5]	training's binary_logloss: 0.439703	valid_0's binary_logloss: 0.408836
[6]	training's binary_logloss: 0.410693	valid_0's binary_logloss: 0.379968
[7]	training's binary_logloss: 0.385842	valid_0's binary_logloss: 0.355201
[8]	training's binary_logloss: 0.364441	valid_0's binary_logloss: 0.333861
[9]	training's binary_logloss: 0.345957	valid_0's binary_logloss: 0.315475
[10]	training's binary_logloss: 0.32994	valid_0's binary_logloss: 0.299534
[11]	training's binary_logloss: 0.316049	valid_0's binary_logloss: 0.285694
[12]	training's binary_logloss: 0.303976	valid_0's binary_logloss: 0.273737
[13]	training's binary_logloss: 0.293471	valid_0's binary_logloss: 0.263352
[14]	training's binary_l

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


...

[1]	training's binary_logloss: 0.614469	valid_0's binary_logloss: 0.679523
[2]	training's binary_logloss: 0.557809	valid_0's binary_logloss: 0.602648
[3]	training's binary_logloss: 0.510889	valid_0's binary_logloss: 0.538888
[4]	training's binary_logloss: 0.471566	valid_0's binary_logloss: 0.485018
[5]	training's binary_logloss: 0.438308	valid_0's binary_logloss: 0.439098
[6]	training's binary_logloss: 0.410007	valid_0's binary_logloss: 0.39964
[7]	training's binary_logloss: 0.385758	valid_0's binary_logloss: 0.36547
[8]	training's binary_logloss: 0.36493	valid_0's binary_logloss: 0.33588
[9]	training's binary_logloss: 0.346972	valid_0's binary_logloss: 0.310014
[10]	training's binary_logloss: 0.331445	valid_0's binary_logloss: 0.287194
[11]	training's binary_logloss: 0.317984	valid_0's binary_logloss: 0.267164
[12]	training's binary_logloss: 0.306302	valid_0's binary_logloss: 0.249362
[13]	training's binary_logloss: 0.296131	valid_0's binary_logloss: 0.233536
[14]	training's binary_lo

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.619903	valid_0's binary_logloss: 0.567708
[2]	training's binary_logloss: 0.562134	valid_0's binary_logloss: 0.514463
[3]	training's binary_logloss: 0.514195	valid_0's binary_logloss: 0.469859
[4]	training's binary_logloss: 0.473952	valid_0's binary_logloss: 0.432137
[5]	training's binary_logloss: 0.439897	valid_0's binary_logloss: 0.399873
[6]	training's binary_logloss: 0.410874	valid_0's binary_logloss: 0.372279
[7]	training's binary_logloss: 0.385992	valid_0's binary_logloss: 0.348143
[8]	training's binary_logloss: 0.364607	valid_0's binary_logloss: 0.327497
[9]	training's binary_logloss: 0.346136	valid_0's binary_logloss: 0.309272
[10]	training's binary_logloss: 0.330147	valid_0's binary_logloss: 0.293606
[11]	training's binary_logloss: 0.316288	valid_0's binary_logloss: 0.279874
[12]	training's binary_logloss: 0.304252	valid_0's binary_logloss: 0.267633
[13]	training's binary_logloss: 0.293773	valid_0's binary_logloss: 0.256944
[14]	training's binar

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.614763	valid_0's binary_logloss: 0.674558
[2]	training's binary_logloss: 0.5581	valid_0's binary_logloss: 0.599344
[3]	training's binary_logloss: 0.511165	valid_0's binary_logloss: 0.536693
[4]	training's binary_logloss: 0.471843	valid_0's binary_logloss: 0.483876
[5]	training's binary_logloss: 0.438595	valid_0's binary_logloss: 0.438834
[6]	training's binary_logloss: 0.410269	valid_0's binary_logloss: 0.400014
[7]	training's binary_logloss: 0.386	valid_0's binary_logloss: 0.366335
[8]	training's binary_logloss: 0.365154	valid_0's binary_logloss: 0.337042
[9]	training's binary_logloss: 0.347177	valid_0's binary_logloss: 0.311337
[10]	training's binary_logloss: 0.331605	valid_0's binary_logloss: 0.288741
[11]	training's binary_logloss: 0.31811	valid_0's binary_logloss: 0.268827
[12]	training's binary_logloss: 0.306392	valid_0's binary_logloss: 0.251208
[13]	training's binary_logloss: 0.296221	valid_0's binary_logloss: 0.235599
[14]	training's binary_logl

In [24]:
# Variance

import lightgbm

#Implementing cross validation 
#kf = KFold(n_splits=23, random_state=1, shuffle=True)
model = lightgbm.LGBMClassifier(learning_rate=0.1, n_estimators=100, max_depth=5, random_state=0)

from time import time
import timeit #imports timeit module
start_time = timeit.default_timer() #defines start time so computational time can be calculated

acc_score = [];
Truth = [];
Output = [];
n_estimators_list = []
max_depth_list = []

x_values = ['Var']
# 'StoS', 'StoR', 'StoL', 'RtoS', 'RtoR', 'RtoL', 'LtoS',
#        'LtoR', 'LtoL', 'STD', 'CoefVar', 'Range', 'Volatility', 'ShEn',
#        'AppEn', 'SampEn', 'IQR', 'Var', 'Rmean_Var', 'Mean_Absolute_Deviation'
y_values = ['Rhythm']
df = features_maindf

for idx, subject in enumerate(good_list):
    
    train_index = ~df['Subject'].str.contains(subject)
    test_index = df['Subject'].str.contains(subject)
    X_train , X_test = df.loc[train_index,x_values], df.loc[test_index,x_values]
    y_train , y_test = df.loc[train_index,y_values].values.ravel(), df.loc[test_index,y_values]

    # Create the LightGBM data containers
    model.fit(X_train,y_train,eval_set=[(X_test,y_test),(X_train,y_train)],
          eval_metric='logloss')

    pred_values = model.predict(X_test)
     
    acc = accuracy_score(y_test, pred_values)
    acc_score.append(acc)
    
    Truth.extend(y_test.values.reshape(y_test.shape[0])); ## it is a list
    Output.extend(pred_values); ## it is a list  
    
    #print(model.feature_importances_)
#     Importance = pd.DataFrame({'Importance':(model.feature_importances_*100)}, 
#                           index = (X_train.columns))
#     Importance.sort_values(by = 'Importance', 
#                        axis = 0, 
#                        ascending = True).plot(kind = 'barh', 
#                                               color = 'r')
#     plt.xlabel('Variable Importance')
#     plt.gca().legend_ = None
    #plt.savefig('plot1.png')


elapsed = timeit.default_timer() - start_time #gives total computation time
print("---Run time is %s seconds ---" % elapsed) #prints computation time
print()

print('Accuracy of each fold: \n {}'.format(acc_score))
print()
print('Avg accuracy : \n{}'.format(np.mean(acc_score))); 
print()
print('Std of accuracy : \n{}'.format(np.std(acc_score)))

print(confusion_matrix(Truth, Output))
print(classification_report(Truth, Output))
print(acc_score)
print(elapsed)

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.640527	valid_0's binary_logloss: 0.577327
[2]	training's binary_logloss: 0.599196	valid_0's binary_logloss: 0.53344
[3]	training's binary_logloss: 0.564867	valid_0's binary_logloss: 0.497566
[4]	training's binary_logloss: 0.536098	valid_0's binary_logloss: 0.46799
[5]	training's binary_logloss: 0.511802	valid_0's binary_logloss: 0.443347
[6]	training's binary_logloss: 0.491153	valid_0's binary_logloss: 0.422711
[7]	training's binary_logloss: 0.473507	valid_0's binary_logloss: 0.405358
[8]	training's binary_logloss: 0.45837	valid_0's binary_logloss: 0.390703
[9]	training's binary_logloss: 0.44534	valid_0's binary_logloss: 0.378238
[10]	training's binary_logloss: 0.434097	valid_0's binary_logloss: 0.367702
[11]	training's binary_logloss: 0.42437	valid_0's binary_logloss: 0.35871
[12]	training's binary_logloss: 0.415939	valid_0's binary_logloss: 0.351099
[13]	training's binary_logloss: 0.408619	valid_0's binary_logloss: 0.344604
[14]	training's binary_logl

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.641073	valid_0's binary_logloss: 0.591789
[2]	training's binary_logloss: 0.60074	valid_0's binary_logloss: 0.538802
[3]	training's binary_logloss: 0.567233	valid_0's binary_logloss: 0.494444
[4]	training's binary_logloss: 0.539151	valid_0's binary_logloss: 0.456788
[5]	training's binary_logloss: 0.515454	valid_0's binary_logloss: 0.42452
[6]	training's binary_logloss: 0.495293	valid_0's binary_logloss: 0.396801
[7]	training's binary_logloss: 0.478053	valid_0's binary_logloss: 0.372787
[8]	training's binary_logloss: 0.463271	valid_0's binary_logloss: 0.351878
[9]	training's binary_logloss: 0.450552	valid_0's binary_logloss: 0.333614
[10]	training's binary_logloss: 0.439576	valid_0's binary_logloss: 0.317638
[11]	training's binary_logloss: 0.430082	valid_0's binary_logloss: 0.303646
[12]	training's binary_logloss: 0.421853	valid_0's binary_logloss: 0.2913
[13]	training's binary_logloss: 0.414696	valid_0's binary_logloss: 0.280427
[14]	training's binary_lo

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


...

[27]	training's binary_logloss: 0.370203	valid_0's binary_logloss: 0.261356
[28]	training's binary_logloss: 0.369237	valid_0's binary_logloss: 0.258999
[29]	training's binary_logloss: 0.368382	valid_0's binary_logloss: 0.2569
[30]	training's binary_logloss: 0.367636	valid_0's binary_logloss: 0.254932
[31]	training's binary_logloss: 0.366969	valid_0's binary_logloss: 0.253189
[32]	training's binary_logloss: 0.366392	valid_0's binary_logloss: 0.251615
[33]	training's binary_logloss: 0.365883	valid_0's binary_logloss: 0.250207
[34]	training's binary_logloss: 0.365441	valid_0's binary_logloss: 0.248951
[35]	training's binary_logloss: 0.365046	valid_0's binary_logloss: 0.247833
[36]	training's binary_logloss: 0.364695	valid_0's binary_logloss: 0.2468
[37]	training's binary_logloss: 0.364393	valid_0's binary_logloss: 0.245902
[38]	training's binary_logloss: 0.364125	valid_0's binary_logloss: 0.245045
[39]	training's binary_logloss: 0.363884	valid_0's binary_logloss: 0.244335
[40]	training's 

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.640276	valid_0's binary_logloss: 0.578678
[2]	training's binary_logloss: 0.599072	valid_0's binary_logloss: 0.534846
[3]	training's binary_logloss: 0.564849	valid_0's binary_logloss: 0.498762
[4]	training's binary_logloss: 0.536195	valid_0's binary_logloss: 0.469035
[5]	training's binary_logloss: 0.511988	valid_0's binary_logloss: 0.443811
[6]	training's binary_logloss: 0.491393	valid_0's binary_logloss: 0.422572
[7]	training's binary_logloss: 0.473803	valid_0's binary_logloss: 0.404543
[8]	training's binary_logloss: 0.458718	valid_0's binary_logloss: 0.389194
[9]	training's binary_logloss: 0.44573	valid_0's binary_logloss: 0.376018
[10]	training's binary_logloss: 0.434521	valid_0's binary_logloss: 0.364742
[11]	training's binary_logloss: 0.424818	valid_0's binary_logloss: 0.355082
[12]	training's binary_logloss: 0.416408	valid_0's binary_logloss: 0.346767
[13]	training's binary_logloss: 0.409108	valid_0's binary_logloss: 0.339564
[14]	training's binary

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.635385	valid_0's binary_logloss: 0.699438
[2]	training's binary_logloss: 0.595261	valid_0's binary_logloss: 0.643676
[3]	training's binary_logloss: 0.561986	valid_0's binary_logloss: 0.596814
[4]	training's binary_logloss: 0.534071	valid_0's binary_logloss: 0.556854
[5]	training's binary_logloss: 0.510493	valid_0's binary_logloss: 0.522567
[6]	training's binary_logloss: 0.490463	valid_0's binary_logloss: 0.492863
[7]	training's binary_logloss: 0.47334	valid_0's binary_logloss: 0.46699
[8]	training's binary_logloss: 0.458652	valid_0's binary_logloss: 0.444408
[9]	training's binary_logloss: 0.446021	valid_0's binary_logloss: 0.424566
[10]	training's binary_logloss: 0.435123	valid_0's binary_logloss: 0.407115
[11]	training's binary_logloss: 0.425697	valid_0's binary_logloss: 0.391703
[12]	training's binary_logloss: 0.417528	valid_0's binary_logloss: 0.378031
[13]	training's binary_logloss: 0.410434	valid_0's binary_logloss: 0.365914
[14]	training's binary_

In [25]:
# Rmean Variance

import lightgbm

#Implementing cross validation 
#kf = KFold(n_splits=23, random_state=1, shuffle=True)
model = lightgbm.LGBMClassifier(learning_rate=0.1, n_estimators=100, max_depth=5, random_state=0)

from time import time
import timeit #imports timeit module
start_time = timeit.default_timer() #defines start time so computational time can be calculated

acc_score = [];
Truth = [];
Output = [];
n_estimators_list = []
max_depth_list = []

x_values = ['Rmean_Var']
# 'StoS', 'StoR', 'StoL', 'RtoS', 'RtoR', 'RtoL', 'LtoS',
#        'LtoR', 'LtoL', 'STD', 'CoefVar', 'Range', 'Volatility', 'ShEn',
#        'AppEn', 'SampEn', 'IQR', 'Var', 'Rmean_Var', 'Mean_Absolute_Deviation'
y_values = ['Rhythm']
df = features_maindf

for idx, subject in enumerate(good_list):
    
    train_index = ~df['Subject'].str.contains(subject)
    test_index = df['Subject'].str.contains(subject)
    X_train , X_test = df.loc[train_index,x_values], df.loc[test_index,x_values]
    y_train , y_test = df.loc[train_index,y_values].values.ravel(), df.loc[test_index,y_values]

    # Create the LightGBM data containers
    model.fit(X_train,y_train,eval_set=[(X_test,y_test),(X_train,y_train)],
          eval_metric='logloss')

    pred_values = model.predict(X_test)
     
    acc = accuracy_score(y_test, pred_values)
    acc_score.append(acc)
    
    Truth.extend(y_test.values.reshape(y_test.shape[0])); ## it is a list
    Output.extend(pred_values); ## it is a list  
    
    #print(model.feature_importances_)
#     Importance = pd.DataFrame({'Importance':(model.feature_importances_*100)}, 
#                           index = (X_train.columns))
#     Importance.sort_values(by = 'Importance', 
#                        axis = 0, 
#                        ascending = True).plot(kind = 'barh', 
#                                               color = 'r')
#     plt.xlabel('Variable Importance')
#     plt.gca().legend_ = None
    #plt.savefig('plot1.png')


elapsed = timeit.default_timer() - start_time #gives total computation time
print("---Run time is %s seconds ---" % elapsed) #prints computation time
print()

print('Accuracy of each fold: \n {}'.format(acc_score))
print()
print('Avg accuracy : \n{}'.format(np.mean(acc_score))); 
print()
print('Std of accuracy : \n{}'.format(np.std(acc_score)))

print(confusion_matrix(Truth, Output))
print(classification_report(Truth, Output))
print(acc_score)
print(elapsed)

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.652791	valid_0's binary_logloss: 0.571171
[2]	training's binary_logloss: 0.621507	valid_0's binary_logloss: 0.521474
[3]	training's binary_logloss: 0.595481	valid_0's binary_logloss: 0.480023
[4]	training's binary_logloss: 0.573689	valid_0's binary_logloss: 0.445158
[5]	training's binary_logloss: 0.555362	valid_0's binary_logloss: 0.415594
[6]	training's binary_logloss: 0.539743	valid_0's binary_logloss: 0.390397
[7]	training's binary_logloss: 0.526468	valid_0's binary_logloss: 0.368785
[8]	training's binary_logloss: 0.515109	valid_0's binary_logloss: 0.349483
[9]	training's binary_logloss: 0.505273	valid_0's binary_logloss: 0.333445
[10]	training's binary_logloss: 0.496881	valid_0's binary_logloss: 0.31884
[11]	training's binary_logloss: 0.489615	valid_0's binary_logloss: 0.306295
[12]	training's binary_logloss: 0.483242	valid_0's binary_logloss: 0.295781
[13]	training's binary_logloss: 0.477736	valid_0's binary_logloss: 0.286029
[14]	training's binary

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.647405	valid_0's binary_logloss: 0.665958
[2]	training's binary_logloss: 0.612282	valid_0's binary_logloss: 0.67735
[3]	training's binary_logloss: 0.583156	valid_0's binary_logloss: 0.689224
[4]	training's binary_logloss: 0.558765	valid_0's binary_logloss: 0.701665
[5]	training's binary_logloss: 0.538192	valid_0's binary_logloss: 0.713618
[6]	training's binary_logloss: 0.520726	valid_0's binary_logloss: 0.725358
[7]	training's binary_logloss: 0.505825	valid_0's binary_logloss: 0.73698
[8]	training's binary_logloss: 0.493063	valid_0's binary_logloss: 0.747875
[9]	training's binary_logloss: 0.482094	valid_0's binary_logloss: 0.758171
[10]	training's binary_logloss: 0.472639	valid_0's binary_logloss: 0.767939
[11]	training's binary_logloss: 0.464469	valid_0's binary_logloss: 0.776995
[12]	training's binary_logloss: 0.457396	valid_0's binary_logloss: 0.78554
[13]	training's binary_logloss: 0.451251	valid_0's binary_logloss: 0.793473
[14]	training's binary_l

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


...

[1]	training's binary_logloss: 0.646597	valid_0's binary_logloss: 0.714198
[2]	training's binary_logloss: 0.615858	valid_0's binary_logloss: 0.664338
[3]	training's binary_logloss: 0.590355	valid_0's binary_logloss: 0.622401
[4]	training's binary_logloss: 0.568985	valid_0's binary_logloss: 0.586733
[5]	training's binary_logloss: 0.550944	valid_0's binary_logloss: 0.556209
[6]	training's binary_logloss: 0.535666	valid_0's binary_logloss: 0.529644
[7]	training's binary_logloss: 0.522579	valid_0's binary_logloss: 0.506697
[8]	training's binary_logloss: 0.511357	valid_0's binary_logloss: 0.486489
[9]	training's binary_logloss: 0.50171	valid_0's binary_logloss: 0.468802
[10]	training's binary_logloss: 0.49339	valid_0's binary_logloss: 0.453232
[11]	training's binary_logloss: 0.486212	valid_0's binary_logloss: 0.439316
[12]	training's binary_logloss: 0.47997	valid_0's binary_logloss: 0.427111
[13]	training's binary_logloss: 0.474552	valid_0's binary_logloss: 0.416336
[14]	training's binary_l

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[22]	training's binary_logloss: 0.452797	valid_0's binary_logloss: 0.163995
[23]	training's binary_logloss: 0.451384	valid_0's binary_logloss: 0.160017
[24]	training's binary_logloss: 0.450146	valid_0's binary_logloss: 0.156471
[25]	training's binary_logloss: 0.44905	valid_0's binary_logloss: 0.153255
[26]	training's binary_logloss: 0.44809	valid_0's binary_logloss: 0.15038
[27]	training's binary_logloss: 0.447214	valid_0's binary_logloss: 0.147698
[28]	training's binary_logloss: 0.446455	valid_0's binary_logloss: 0.145328
[29]	training's binary_logloss: 0.445783	valid_0's binary_logloss: 0.143182
[30]	training's binary_logloss: 0.445165	valid_0's binary_logloss: 0.141317
[31]	training's binary_logloss: 0.444614	valid_0's binary_logloss: 0.139518
[32]	training's binary_logloss: 0.444129	valid_0's binary_logloss: 0.137908
[33]	training's binary_logloss: 0.443701	valid_0's binary_logloss: 0.136474
[34]	training's binary_logloss: 0.443323	valid_0's binary_logloss: 0.13523
[35]	training's 

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.646908	valid_0's binary_logloss: 0.705115
[2]	training's binary_logloss: 0.616288	valid_0's binary_logloss: 0.654211
[3]	training's binary_logloss: 0.590876	valid_0's binary_logloss: 0.611361
[4]	training's binary_logloss: 0.569683	valid_0's binary_logloss: 0.574911
[5]	training's binary_logloss: 0.551688	valid_0's binary_logloss: 0.543649
[6]	training's binary_logloss: 0.536403	valid_0's binary_logloss: 0.516539
[7]	training's binary_logloss: 0.523355	valid_0's binary_logloss: 0.492989
[8]	training's binary_logloss: 0.512168	valid_0's binary_logloss: 0.472435
[9]	training's binary_logloss: 0.502604	valid_0's binary_logloss: 0.454337
[10]	training's binary_logloss: 0.494295	valid_0's binary_logloss: 0.438453
[11]	training's binary_logloss: 0.48716	valid_0's binary_logloss: 0.42436
[12]	training's binary_logloss: 0.480975	valid_0's binary_logloss: 0.411893
[13]	training's binary_logloss: 0.475605	valid_0's binary_logloss: 0.400848
[14]	training's binary_

In [26]:
# Mean Absolute Deviation

import lightgbm

#Implementing cross validation 
#kf = KFold(n_splits=23, random_state=1, shuffle=True)
model = lightgbm.LGBMClassifier(learning_rate=0.1, n_estimators=100, max_depth=5, random_state=0)

from time import time
import timeit #imports timeit module
start_time = timeit.default_timer() #defines start time so computational time can be calculated

acc_score = [];
Truth = [];
Output = [];
n_estimators_list = []
max_depth_list = []

x_values = ['Mean_Absolute_Deviation']
# 'StoS', 'StoR', 'StoL', 'RtoS', 'RtoR', 'RtoL', 'LtoS',
#        'LtoR', 'LtoL', 'STD', 'CoefVar', 'Range', 'Volatility', 'ShEn',
#        'AppEn', 'SampEn', 'IQR', 'Var', 'Rmean_Var', 'Mean_Absolute_Deviation'
y_values = ['Rhythm']
df = features_maindf

for idx, subject in enumerate(good_list):
    
    train_index = ~df['Subject'].str.contains(subject)
    test_index = df['Subject'].str.contains(subject)
    X_train , X_test = df.loc[train_index,x_values], df.loc[test_index,x_values]
    y_train , y_test = df.loc[train_index,y_values].values.ravel(), df.loc[test_index,y_values]

    # Create the LightGBM data containers
    model.fit(X_train,y_train,eval_set=[(X_test,y_test),(X_train,y_train)],
          eval_metric='logloss')

    pred_values = model.predict(X_test)
     
    acc = accuracy_score(y_test, pred_values)
    acc_score.append(acc)
    
    Truth.extend(y_test.values.reshape(y_test.shape[0])); ## it is a list
    Output.extend(pred_values); ## it is a list  
    
    #print(model.feature_importances_)
#     Importance = pd.DataFrame({'Importance':(model.feature_importances_*100)}, 
#                           index = (X_train.columns))
#     Importance.sort_values(by = 'Importance', 
#                        axis = 0, 
#                        ascending = True).plot(kind = 'barh', 
#                                               color = 'r')
#     plt.xlabel('Variable Importance')
#     plt.gca().legend_ = None
    #plt.savefig('plot1.png')


elapsed = timeit.default_timer() - start_time #gives total computation time
print("---Run time is %s seconds ---" % elapsed) #prints computation time
print()

print('Accuracy of each fold: \n {}'.format(acc_score))
print()
print('Avg accuracy : \n{}'.format(np.mean(acc_score))); 
print()
print('Std of accuracy : \n{}'.format(np.std(acc_score)))

print(confusion_matrix(Truth, Output))
print(classification_report(Truth, Output))
print(acc_score)
print(elapsed)

[1]	training's binary_logloss: 0.631934	valid_0's binary_logloss: 0.572801


C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[2]	training's binary_logloss: 0.583571	valid_0's binary_logloss: 0.52518
[3]	training's binary_logloss: 0.543426	valid_0's binary_logloss: 0.486144
[4]	training's binary_logloss: 0.509763	valid_0's binary_logloss: 0.453829
[5]	training's binary_logloss: 0.481319	valid_0's binary_logloss: 0.426819
[6]	training's binary_logloss: 0.457096	valid_0's binary_logloss: 0.404261
[7]	training's binary_logloss: 0.436378	valid_0's binary_logloss: 0.385314
[8]	training's binary_logloss: 0.418583	valid_0's binary_logloss: 0.369336
[9]	training's binary_logloss: 0.403249	valid_0's binary_logloss: 0.355806
[10]	training's binary_logloss: 0.389997	valid_0's binary_logloss: 0.344382
[11]	training's binary_logloss: 0.378522	valid_0's binary_logloss: 0.334735
[12]	training's binary_logloss: 0.368565	valid_0's binary_logloss: 0.326531
[13]	training's binary_logloss: 0.359914	valid_0's binary_logloss: 0.319705
[14]	training's binary_logloss: 0.352389	valid_0's binary_logloss: 0.313842
[15]	training's binar

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.632141	valid_0's binary_logloss: 0.589573
[2]	training's binary_logloss: 0.584557	valid_0's binary_logloss: 0.53484
[3]	training's binary_logloss: 0.54506	valid_0's binary_logloss: 0.489057
[4]	training's binary_logloss: 0.511938	valid_0's binary_logloss: 0.450302
[5]	training's binary_logloss: 0.483941	valid_0's binary_logloss: 0.41716
[6]	training's binary_logloss: 0.460136	valid_0's binary_logloss: 0.388666
[7]	training's binary_logloss: 0.439765	valid_0's binary_logloss: 0.364065
[8]	training's binary_logloss: 0.422274	valid_0's binary_logloss: 0.342735
[9]	training's binary_logloss: 0.407215	valid_0's binary_logloss: 0.324108
[10]	training's binary_logloss: 0.394196	valid_0's binary_logloss: 0.307865
[11]	training's binary_logloss: 0.38292	valid_0's binary_logloss: 0.293612
[12]	training's binary_logloss: 0.373138	valid_0's binary_logloss: 0.281215
[13]	training's binary_logloss: 0.36462	valid_0's binary_logloss: 0.270368
[14]	training's binary_log

...

[1]	training's binary_logloss: 0.6267	valid_0's binary_logloss: 0.690316
[2]	training's binary_logloss: 0.579881	valid_0's binary_logloss: 0.621508
[3]	training's binary_logloss: 0.541073	valid_0's binary_logloss: 0.564139
[4]	training's binary_logloss: 0.508542	valid_0's binary_logloss: 0.515323
[5]	training's binary_logloss: 0.481078	valid_0's binary_logloss: 0.473984
[6]	training's binary_logloss: 0.457715	valid_0's binary_logloss: 0.438093
[7]	training's binary_logloss: 0.43775	valid_0's binary_logloss: 0.407026
[8]	training's binary_logloss: 0.420634	valid_0's binary_logloss: 0.380219
[9]	training's binary_logloss: 0.405886	valid_0's binary_logloss: 0.356604
[10]	training's binary_logloss: 0.393153	valid_0's binary_logloss: 0.335801
[11]	training's binary_logloss: 0.382136	valid_0's binary_logloss: 0.317488
[12]	training's binary_logloss: 0.372587	valid_0's binary_logloss: 0.301553
[13]	training's binary_logloss: 0.364291	valid_0's binary_logloss: 0.28741
[14]	training's binary_lo

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[2]	training's binary_logloss: 0.583733	valid_0's binary_logloss: 0.52502
[3]	training's binary_logloss: 0.543821	valid_0's binary_logloss: 0.485101
[4]	training's binary_logloss: 0.510325	valid_0's binary_logloss: 0.451417
[5]	training's binary_logloss: 0.482009	valid_0's binary_logloss: 0.422968
[6]	training's binary_logloss: 0.457919	valid_0's binary_logloss: 0.398805
[7]	training's binary_logloss: 0.437319	valid_0's binary_logloss: 0.378187
[8]	training's binary_logloss: 0.419639	valid_0's binary_logloss: 0.360493
[9]	training's binary_logloss: 0.404395	valid_0's binary_logloss: 0.345323
[10]	training's binary_logloss: 0.391226	valid_0's binary_logloss: 0.332259
[11]	training's binary_logloss: 0.379824	valid_0's binary_logloss: 0.320958
[12]	training's binary_logloss: 0.369932	valid_0's binary_logloss: 0.311215
[13]	training's binary_logloss: 0.361338	valid_0's binary_logloss: 0.302743
[14]	training's binary_logloss: 0.353853	valid_0's binary_logloss: 0.295482
[15]	training's binar

C:\Users\santo\anaconda3\lib\site-packages\sklearn\preprocessing\_label.py:133: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


[1]	training's binary_logloss: 0.626828	valid_0's binary_logloss: 0.687645
[2]	training's binary_logloss: 0.579871	valid_0's binary_logloss: 0.622657
[3]	training's binary_logloss: 0.540927	valid_0's binary_logloss: 0.568254
[4]	training's binary_logloss: 0.508301	valid_0's binary_logloss: 0.522147
[5]	training's binary_logloss: 0.480739	valid_0's binary_logloss: 0.482699
[6]	training's binary_logloss: 0.457299	valid_0's binary_logloss: 0.448674
[7]	training's binary_logloss: 0.437268	valid_0's binary_logloss: 0.419161
[8]	training's binary_logloss: 0.420078	valid_0's binary_logloss: 0.393382
[9]	training's binary_logloss: 0.405278	valid_0's binary_logloss: 0.370844
[10]	training's binary_logloss: 0.392499	valid_0's binary_logloss: 0.350997
[11]	training's binary_logloss: 0.381446	valid_0's binary_logloss: 0.333482
[12]	training's binary_logloss: 0.371861	valid_0's binary_logloss: 0.317985
[13]	training's binary_logloss: 0.36353	valid_0's binary_logloss: 0.304248
[14]	training's binary